# End to end Use of Medallion Architecture

In [0]:
application_id = dbutils.secrets.get(scope="databricksVolt2323",key="app-id")
tenant_id = dbutils.secrets.get(scope="databricksVolt2323",key="tenant-id")
secret = dbutils.secrets.get(scope="databricksVolt2323",key="secret")

In [0]:
# container_name = "silver"
# account_name = "databricksfiles2323"
# mount_point = "/mnt/silver"

container_name = "gold"
account_name = "databricksfiles2323"
mount_point = "/mnt/gold"

In [0]:
configs = {"fs.azure.account.auth.type": "OAuth",
          "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
          "fs.azure.account.oauth2.client.id": application_id,
          "fs.azure.account.oauth2.client.secret": secret,
          "fs.azure.account.oauth2.client.endpoint": f"https://login.microsoftonline.com/{tenant_id}/oauth2/token"}
 
dbutils.fs.mount(
  source = f"abfss://{container_name}@{account_name}.dfs.core.windows.net/",
  mount_point = mount_point,
  extra_configs = configs)

True

In [0]:
orders_path = '/mnt/bronze/orders.csv'
# Reading the orders csv file
# Initially assigning the order_datetime column as a string because it is not in the correct timestamp format
# when defining the schema I will set nullable, which is the third argument in StructField to False, this does not permit null values

# import the relevant data types
from pyspark.sql.types import IntegerType, StringType, DoubleType, StructField, StructType
orders_schema = StructType([
                    StructField("ORDER_ID", IntegerType(), False),
                    StructField("ORDER_DATETIME", StringType(), False),
                    StructField("CUSTOMER_ID", IntegerType(), False),
                    StructField("ORDER_STATUS", StringType(), False),
                    StructField("STORE_ID", IntegerType(), False)
                    ]
                    )

orders=spark.read.csv(path=orders_path, header=True, schema=orders_schema)

In [0]:
# displaying the orders dataframe
orders.display()

ORDER_ID ORDER_DATETIME CUSTOMER_ID ORDER_STATUS STORE_ID 447 06-JAN-22 09.35.42.00 355 COMPLETE 1 448 06-JAN-22 10.23.14.00 155 COMPLETE 1 449 06-JAN-22 01.21.54.00 242 COMPLETE 1 450 06-JAN-22 05.57.04.00 49 COMPLETE 1 451 06-JAN-22 10.39.07.00 204 COMPLETE 1 452 07-JAN-22 01.11.46.00 216 COMPLETE 1 453 07-JAN-22 06.53.06.00 4 COMPLETE 4 454 07-JAN-22 03.55.15.00 388 COMPLETE 1 455 07-JAN-22 06.38.38.00 291 COMPLETE 1 456 08-JAN-22 12.52.12.00 272 COMPLETE 1 457 08-JAN-22 10.13.30.00 307 COMPLETE 1 458 08-JAN-22 11.03.34.00 42 COMPLETE 1 459 09-JAN-22 02.35.19.00 390 COMPLETE 1 460 09-JAN-22 03.35.53.00 235 COMPLETE 1 461 09-JAN-22 12.54.10.00 302 COMPLETE 1 462 09-JAN-22 02.44.45.00 357 COMPLETE 1 463 09-JAN-22 02.54.31.00 271 COMPLETE 1 464 09-JAN-22 05.16.13.00 79 COMPLETE 1 465 09-JAN-22 09.42.53.00 280 COMPLETE 1 466 10-JAN-22 07.42.04.00 210 COMPLETE 7 467 11-JAN-22 01.25.06.00 293 COMPLETE 1 468 12-JAN-22 03.56.35.00 299 CANCELLED 1 469 12-JAN-22 10.22.10.00 239 COMPLETE 1 470 12-JAN-22 11.40.14.00 217 COMPLETE 1 471 12-JAN-22 12.02.56.00 61 COMPLETE 3 472 12-JAN-22 12.40.49.00 182 COMPLETE 1 473 12-JAN-22 01.24.18.00 116 COMPLETE 1 474 12-JAN-22 06.17.28.00 244 COMPLETE 1 475 12-JAN-22 10.20.52.00 210 COMPLETE 1 476 12-JAN-22 10.41.43.00 84 COMPLETE 1 477 13-JAN-22 01.00.02.00 374 COMPLETE 1 478 13-JAN-22 06.17.28.00 389 COMPLETE 1 479 13-JAN-22 07.13.56.00 368 COMPLETE 1 480 13-JAN-22 08.44.34.00 344 COMPLETE 1 481 13-JAN-22 11.40.21.00 118 COMPLETE 1 482 13-JAN-22 01.54.39.00 88 COMPLETE 1 483 13-JAN-22 09.10.36.00 72 COMPLETE 1 484 14-JAN-22 04.30.58.00 159 COMPLETE 1 485 15-JAN-22 05.21.41.00 134 COMPLETE 1 486 15-JAN-22 01.27.37.00 105 COMPLETE 1 487 15-JAN-22 02.04.27.00 259 COMPLETE 1 488 15-JAN-22 06.29.22.00 150 COMPLETE 1 489 15-JAN-22 11.08.12.00 64 REFUNDED 1 490 16-JAN-22 02.18.47.00 48 COMPLETE 1 491 16-JAN-22 11.36.07.00 264 COMPLETE 3 492 16-JAN-22 08.30.25.00 381 COMPLETE 1 493 17-JAN-22 06.17.22.00 155 COMPLETE 1 494 17-JAN-22 09.41.15.00 256 COMPLETE 1 495 17-JAN-22 06.07.00.00 205 COMPLETE 2 496 17-JAN-22 11.58.50.00 33 COMPLETE 4 497 18-JAN-22 12.59.01.00 164 COMPLETE 1 498 18-JAN-22 03.48.04.00 262 COMPLETE 1 499 18-JAN-22 02.11.23.00 333 COMPLETE 1 500 18-JAN-22 03.56.55.00 200 COMPLETE 1 501 18-JAN-22 10.14.50.00 367 COMPLETE 1 502 19-JAN-22 02.50.53.00 355 COMPLETE 1 503 20-JAN-22 06.55.43.00 243 COMPLETE 1 504 21-JAN-22 06.03.09.00 107 COMPLETE 1 505 22-JAN-22 02.08.42.00 248 COMPLETE 1 506 22-JAN-22 05.36.47.00 4 COMPLETE 1 507 22-JAN-22 10.43.04.00 137 COMPLETE 1 508 22-JAN-22 02.47.09.00 157 COMPLETE 1 509 22-JAN-22 04.07.52.00 303 COMPLETE 1 510 22-JAN-22 11.53.07.00 322 COMPLETE 1 511 23-JAN-22 02.08.50.00 22 COMPLETE 1 512 23-JAN-22 09.07.16.00 235 COMPLETE 3 513 24-JAN-22 02.40.25.00 15 COMPLETE 1 514 24-JAN-22 05.30.03.00 63 COMPLETE 1 515 24-JAN-22 03.30.17.00 385 COMPLETE 1 516 24-JAN-22 05.11.24.00 30 COMPLETE 1 517 24-JAN-22 08.54.50.00 302 COMPLETE 1 518 25-JAN-22 07.01.14.00 125 COMPLETE 1 519 25-JAN-22 11.02.55.00 207 COMPLETE 1 520 25-JAN-22 11.27.33.00 35 COMPLETE 6 521 26-JAN-22 03.32.49.00 157 COMPLETE 1 522 26-JAN-22 06.10.38.00 298 COMPLETE 1 523 26-JAN-22 11.33.09.00 60 COMPLETE 1 524 26-JAN-22 12.48.31.00 287 COMPLETE 1 525 26-JAN-22 05.01.17.00 43 COMPLETE 1 526 26-JAN-22 06.56.42.00 127 REFUNDED 1 527 27-JAN-22 04.36.29.00 272 COMPLETE 1 528 27-JAN-22 06.57.51.00 143 COMPLETE 1 529 27-JAN-22 07.48.59.00 253 COMPLETE 1 530 27-JAN-22 08.18.37.00 311 COMPLETE 1 531 27-JAN-22 12.50.09.00 237 COMPLETE 1 532 28-JAN-22 08.05.40.00 251 COMPLETE 1 533 28-JAN-22 12.55.59.00 130 COMPLETE 1 534 28-JAN-22 03.08.46.00 362 COMPLETE 1 535 29-JAN-22 12.06.37.00 319 COMPLETE 1 536 29-JAN-22 07.57.30.00 370 COMPLETE 1 537 29-JAN-22 01.36.37.00 49 COMPLETE 1 538 30-JAN-22 04.05.58.00 385 COMPLETE 1 539 30-JAN-22 09.47.01.00 31 CANCELLED 1 540 30-JAN-22 11.09.41.00 41 COMPLETE 1 541 30-JAN-22 02.15.41.00 173 COMPLETE 1 542 31-JAN-22 01.01.48.00 216 COMPLETE 1 543 31-JAN-22 02.09.48.00 35

In [0]:
# Importing the to_timestamp function
from pyspark.sql.functions import to_timestamp

In [0]:
# Converting the order_datetime column to a timestamp and aliasing the name as 'order_timestamp'

orders = orders.select('ORDER_ID', \
              to_timestamp(orders['order_datetime'], "dd-MMM-yy kk.mm.ss.SS").alias('ORDER_TIMESTAMP'), \
              'CUSTOMER_ID', \
              'ORDER_STATUS', \
              'STORE_ID'
             )

In [0]:
# Confirming the data types
orders.dtypes

[('ORDER_ID', 'int'),
 ('ORDER_TIMESTAMP', 'timestamp'),
 ('CUSTOMER_ID', 'int'),
 ('ORDER_STATUS', 'string'),
 ('STORE_ID', 'int')]

In [0]:
# reviewing the current state of the orders dataframe
orders.display()

ORDER_ID ORDER_TIMESTAMP CUSTOMER_ID ORDER_STATUS STORE_ID 447 2022-01-06T09:35:42Z 355 COMPLETE 1 448 2022-01-06T10:23:14Z 155 COMPLETE 1 449 2022-01-06T01:21:54Z 242 COMPLETE 1 450 2022-01-06T05:57:04Z 49 COMPLETE 1 451 2022-01-06T10:39:07Z 204 COMPLETE 1 452 2022-01-07T01:11:46Z 216 COMPLETE 1 453 2022-01-07T06:53:06Z 4 COMPLETE 4 454 2022-01-07T03:55:15Z 388 COMPLETE 1 455 2022-01-07T06:38:38Z 291 COMPLETE 1 456 2022-01-08T12:52:12Z 272 COMPLETE 1 457 2022-01-08T10:13:30Z 307 COMPLETE 1 458 2022-01-08T11:03:34Z 42 COMPLETE 1 459 2022-01-09T02:35:19Z 390 COMPLETE 1 460 2022-01-09T03:35:53Z 235 COMPLETE 1 461 2022-01-09T12:54:10Z 302 COMPLETE 1 462 2022-01-09T02:44:45Z 357 COMPLETE 1 463 2022-01-09T02:54:31Z 271 COMPLETE 1 464 2022-01-09T05:16:13Z 79 COMPLETE 1 465 2022-01-09T09:42:53Z 280 COMPLETE 1 466 2022-01-10T07:42:04Z 210 COMPLETE 7 467 2022-01-11T01:25:06Z 293 COMPLETE 1 468 2022-01-12T03:56:35Z 299 CANCELLED 1 469 2022-01-12T10:22:10Z 239 COMPLETE 1 470 2022-01-12T11:40:14Z 217 COMPLETE 1 471 2022-01-12T12:02:56Z 61 COMPLETE 3 472 2022-01-12T12:40:49Z 182 COMPLETE 1 473 2022-01-12T01:24:18Z 116 COMPLETE 1 474 2022-01-12T06:17:28Z 244 COMPLETE 1 475 2022-01-12T10:20:52Z 210 COMPLETE 1 476 2022-01-12T10:41:43Z 84 COMPLETE 1 477 2022-01-13T01:00:02Z 374 COMPLETE 1 478 2022-01-13T06:17:28Z 389 COMPLETE 1 479 2022-01-13T07:13:56Z 368 COMPLETE 1 480 2022-01-13T08:44:34Z 344 COMPLETE 1 481 2022-01-13T11:40:21Z 118 COMPLETE 1 482 2022-01-13T01:54:39Z 88 COMPLETE 1 483 2022-01-13T09:10:36Z 72 COMPLETE 1 484 2022-01-14T04:30:58Z 159 COMPLETE 1 485 2022-01-15T05:21:41Z 134 COMPLETE 1 486 2022-01-15T01:27:37Z 105 COMPLETE 1 487 2022-01-15T02:04:27Z 259 COMPLETE 1 488 2022-01-15T06:29:22Z 150 COMPLETE 1 489 2022-01-15T11:08:12Z 64 REFUNDED 1 490 2022-01-16T02:18:47Z 48 COMPLETE 1 491 2022-01-16T11:36:07Z 264 COMPLETE 3 492 2022-01-16T08:30:25Z 381 COMPLETE 1 493 2022-01-17T06:17:22Z 155 COMPLETE 1 494 2022-01-17T09:41:15Z 256 COMPLETE 1 495 2022-01-17T06:07:00Z 205 COMPLETE 2 496 2022-01-17T11:58:50Z 33 COMPLETE 4 497 2022-01-18T12:59:01Z 164 COMPLETE 1 498 2022-01-18T03:48:04Z 262 COMPLETE 1 499 2022-01-18T02:11:23Z 333 COMPLETE 1 500 2022-01-18T03:56:55Z 200 COMPLETE 1 501 2022-01-18T10:14:50Z 367 COMPLETE 1 502 2022-01-19T02:50:53Z 355 COMPLETE 1 503 2022-01-20T06:55:43Z 243 COMPLETE 1 504 2022-01-21T06:03:09Z 107 COMPLETE 1 505 2022-01-22T02:08:42Z 248 COMPLETE 1 506 2022-01-22T05:36:47Z 4 COMPLETE 1 507 2022-01-22T10:43:04Z 137 COMPLETE 1 508 2022-01-22T02:47:09Z 157 COMPLETE 1 509 2022-01-22T04:07:52Z 303 COMPLETE 1 510 2022-01-22T11:53:07Z 322 COMPLETE 1 511 2022-01-23T02:08:50Z 22 COMPLETE 1 512 2022-01-23T09:07:16Z 235 COMPLETE 3 513 2022-01-24T02:40:25Z 15 COMPLETE 1 514 2022-01-24T05:30:03Z 63 COMPLETE 1 515 2022-01-24T03:30:17Z 385 COMPLETE 1 516 2022-01-24T05:11:24Z 30 COMPLETE 1 517 2022-01-24T08:54:50Z 302 COMPLETE 1 518 2022-01-25T07:01:14Z 125 COMPLETE 1 519 2022-01-25T11:02:55Z 207 COMPLETE 1 520 2022-01-25T11:27:33Z 35 COMPLETE 6 521 2022-01-26T03:32:49Z 157 COMPLETE 1 522 2022-01-26T06:10:38Z 298 COMPLETE 1 523 2022-01-26T11:33:09Z 60 COMPLETE 1 524 2022-01-26T12:48:31Z 287 COMPLETE 1 525 2022-01-26T05:01:17Z 43 COMPLETE 1 526 2022-01-26T06:56:42Z 127 REFUNDED 1 527 2022-01-27T04:36:29Z 272 COMPLETE 1 528 2022-01-27T06:57:51Z 143 COMPLETE 1 529 2022-01-27T07:48:59Z 253 COMPLETE 1 530 2022-01-27T08:18:37Z 311 COMPLETE 1 531 2022-01-27T12:50:09Z 237 COMPLETE 1 532 2022-01-28T08:05:40Z 251 COMPLETE 1 533 2022-01-28T12:55:59Z 130 COMPLETE 1 534 2022-01-28T03:08:46Z 362 COMPLETE 1 535 2022-01-29T12:06:37Z 319 COMPLETE 1 536 2022-01-29T07:57:30Z 370 COMPLETE 1 537 2022-01-29T01:36:37Z 49 COMPLETE 1 538 2022-01-30T04:05:58Z 385 COMPLETE 1 539 2022-01-30T09:47:01Z 31 CANCELLED 1 540 2022-01-30T11:09:41Z 41 COMPLETE 1 541 2022-01-30T02:15:41Z 173 COMPLETE 1 542 2022-01-31T01:01:48Z 216 COMPLETE 1 543 2022-01-31T02:09:48Z 357 COMPLETE 9 544 2022-01-31T01:12:13Z 3 COMPLETE 1 545 2022-01-31T02:23:17Z 35 COMPLETE 1 546 20

In [0]:
# filtering the records to display only 'COMPLETE' orders
# assigning the result back to the orders dataframe
orders = orders.filter(orders['order_status']=="COMPLETE")

In [0]:
# Reading the stores csv file

stores_path = "/mnt/bronze/stores.csv"

stores_schema = StructType([
                    StructField("STORE_ID", IntegerType(), False),
                    StructField("STORE_NAME", StringType(), False),
                    StructField("WEB_ADDRESS", StringType(), False),
                    StructField("LATITUDE", DoubleType(), False),
                    StructField("LONGITUDE", DoubleType(), False)
                    ]
                    )

stores=spark.read.csv(path=stores_path, header=True, schema=stores_schema)

In [0]:
# displaying the stores dataframe
stores.display()

STORE_ID STORE_NAME WEB_ADDRESS LATITUDE LONGITUDE 1 Online https://www.example.com null null 2 San Francisco null 37.529395 -122.267237 3 Seattle null 47.6053 -122.33221 4 New York City null 40.745216 -73.980518 5 Chicago null 41.878751 -87.636675 6 London null 51.519281 -0.087296 7 Bucharest null 44.43225 26.10626 8 Berlin null 52.5161 13.3873 9 Utrecht null 52.103263 5.061644 10 Madrid null 40.4929 -3.8737 11 Johannesburg null -26.044222 28.094662 12 Lagos null 6.42806 3.42199 13 Bengaluru null 12.8939 77.5978 14 Mumbai null 19.069405 72.870143 15 New Dehli null 28.527693 77.220135 16 Sydney null -33.797279 151.143826 17 Perth null -31.953715 115.851645 18 S�o Paulo null -23.5475 -46.63611 19 Buenos Aires null -34.61016 -58.362867 20 Mexico City null 19.428489 -99.205745 21 Bejing null 40.0572 116.290061 22 Tokyo null 35.671534 139.718584 23 Tel Aviv null 32.100664 34.862138

In [0]:
# joining the orders and stores via a 'left' join, the orders table is the left table.
# this operation adds the store_name to the orders dataframe
# the final operation is a select method to select only the required columns and assign it back to the orders dataframe

orders = orders.join(stores, orders['store_id']==stores['store_id'], 'left').select('ORDER_ID', 'ORDER_TIMESTAMP', 'CUSTOMER_ID', 'STORE_NAME')

In [0]:
# the orders dataframe is ready to move to the silver layer
orders.display()

ORDER_ID ORDER_TIMESTAMP CUSTOMER_ID STORE_NAME 447 2022-01-06T09:35:42Z 355 Online 448 2022-01-06T10:23:14Z 155 Online 449 2022-01-06T01:21:54Z 242 Online 450 2022-01-06T05:57:04Z 49 Online 451 2022-01-06T10:39:07Z 204 Online 452 2022-01-07T01:11:46Z 216 Online 453 2022-01-07T06:53:06Z 4 New York City 454 2022-01-07T03:55:15Z 388 Online 455 2022-01-07T06:38:38Z 291 Online 456 2022-01-08T12:52:12Z 272 Online 457 2022-01-08T10:13:30Z 307 Online 458 2022-01-08T11:03:34Z 42 Online 459 2022-01-09T02:35:19Z 390 Online 460 2022-01-09T03:35:53Z 235 Online 461 2022-01-09T12:54:10Z 302 Online 462 2022-01-09T02:44:45Z 357 Online 463 2022-01-09T02:54:31Z 271 Online 464 2022-01-09T05:16:13Z 79 Online 465 2022-01-09T09:42:53Z 280 Online 466 2022-01-10T07:42:04Z 210 Bucharest 467 2022-01-11T01:25:06Z 293 Online 469 2022-01-12T10:22:10Z 239 Online 470 2022-01-12T11:40:14Z 217 Online 471 2022-01-12T12:02:56Z 61 Seattle 472 2022-01-12T12:40:49Z 182 Online 473 2022-01-12T01:24:18Z 116 Online 474 2022-01-12T06:17:28Z 244 Online 475 2022-01-12T10:20:52Z 210 Online 476 2022-01-12T10:41:43Z 84 Online 477 2022-01-13T01:00:02Z 374 Online 478 2022-01-13T06:17:28Z 389 Online 479 2022-01-13T07:13:56Z 368 Online 480 2022-01-13T08:44:34Z 344 Online 481 2022-01-13T11:40:21Z 118 Online 482 2022-01-13T01:54:39Z 88 Online 483 2022-01-13T09:10:36Z 72 Online 484 2022-01-14T04:30:58Z 159 Online 485 2022-01-15T05:21:41Z 134 Online 486 2022-01-15T01:27:37Z 105 Online 487 2022-01-15T02:04:27Z 259 Online 488 2022-01-15T06:29:22Z 150 Online 490 2022-01-16T02:18:47Z 48 Online 491 2022-01-16T11:36:07Z 264 Seattle 492 2022-01-16T08:30:25Z 381 Online 493 2022-01-17T06:17:22Z 155 Online 494 2022-01-17T09:41:15Z 256 Online 495 2022-01-17T06:07:00Z 205 San Francisco 496 2022-01-17T11:58:50Z 33 New York City 497 2022-01-18T12:59:01Z 164 Online 498 2022-01-18T03:48:04Z 262 Online 499 2022-01-18T02:11:23Z 333 Online 500 2022-01-18T03:56:55Z 200 Online 501 2022-01-18T10:14:50Z 367 Online 502 2022-01-19T02:50:53Z 355 Online 503 2022-01-20T06:55:43Z 243 Online 504 2022-01-21T06:03:09Z 107 Online 505 2022-01-22T02:08:42Z 248 Online 506 2022-01-22T05:36:47Z 4 Online 507 2022-01-22T10:43:04Z 137 Online 508 2022-01-22T02:47:09Z 157 Online 509 2022-01-22T04:07:52Z 303 Online 510 2022-01-22T11:53:07Z 322 Online 511 2022-01-23T02:08:50Z 22 Online 512 2022-01-23T09:07:16Z 235 Seattle 513 2022-01-24T02:40:25Z 15 Online 514 2022-01-24T05:30:03Z 63 Online 515 2022-01-24T03:30:17Z 385 Online 516 2022-01-24T05:11:24Z 30 Online 517 2022-01-24T08:54:50Z 302 Online 518 2022-01-25T07:01:14Z 125 Online 519 2022-01-25T11:02:55Z 207 Online 520 2022-01-25T11:27:33Z 35 London 521 2022-01-26T03:32:49Z 157 Online 522 2022-01-26T06:10:38Z 298 Online 523 2022-01-26T11:33:09Z 60 Online 524 2022-01-26T12:48:31Z 287 Online 525 2022-01-26T05:01:17Z 43 Online 527 2022-01-27T04:36:29Z 272 Online 528 2022-01-27T06:57:51Z 143 Online 529 2022-01-27T07:48:59Z 253 Online 530 2022-01-27T08:18:37Z 311 Online 531 2022-01-27T12:50:09Z 237 Online 532 2022-01-28T08:05:40Z 251 Online 533 2022-01-28T12:55:59Z 130 Online 534 2022-01-28T03:08:46Z 362 Online 535 2022-01-29T12:06:37Z 319 Online 536 2022-01-29T07:57:30Z 370 Online 537 2022-01-29T01:36:37Z 49 Online 538 2022-01-30T04:05:58Z 385 Online 540 2022-01-30T11:09:41Z 41 Online 541 2022-01-30T02:15:41Z 173 Online 542 2022-01-31T01:01:48Z 216 Online 543 2022-01-31T02:09:48Z 357 Utrecht 544 2022-01-31T01:12:13Z 3 Online 545 2022-01-31T02:23:17Z 35 Online 546 2022-01-31T03:15:43Z 60 San Francisco 547 2022-02-01T02:49:11Z 72 Online 548 2022-02-01T11:35:24Z 140 Online 549 2022-02-01T12:43:49Z 385 Berlin 550 2022-02-01T02:42:29Z 313 Online 551 2022-02-01T06:59:51Z 190 Online 552 2022-02-02T01:42:52Z 209 London 553 2022-02-02T10:21:55Z 35 Online 554 2022-02-02T10:51:55Z 93 Online 555 2022-02-02T01:30:47Z 105 Online 556 2022-02-02T06:06:57Z 143 Online 557 2022-02-02T07:26:21Z 221 Online 558 2022-02-02T10:49:37Z 206 Seattle 559 2022-02-03T02:56:32Z 38 Online 560 2022-02-03T06:13:1

In [0]:
# writing the orders dataframe as a parquet file in the silver layer, should use mode = 'overwrite' in this instance
orders.write.parquet("/mnt/silver/orders", mode='overwrite')

#### ORDER_ITEMS

Save a table called ORDER_ITEMS in the silver layer, it should contain the following columns:
- ORDER_ID, type INTEGER
- PRODUCT_ID, type INTEGER
- UNIT_PRICE, type DOUBLE
- QUANTITY, type INTEGER

The file should be saved in PARQUET format.

In [0]:
# Reading the order items csv file

order_items_path = "/mnt/bronze/order_items.csv"

order_items_schema = StructType([
                    StructField("ORDER_ID", IntegerType(), False),
                    StructField("LINE_ITEM_ID", IntegerType(), False),
                    StructField("PRODUCT_ID", IntegerType(), False),
                    StructField("UNIT_PRICE", DoubleType(), False),
                    StructField("QUANTITY", IntegerType(), False)
                    ]
                    )

order_items=spark.read.csv(path=order_items_path, header=True, schema=order_items_schema)

In [0]:
# reviewing the order_items dataframe, the line_item_id column can be removed
order_items.display()

ORDER_ID LINE_ITEM_ID PRODUCT_ID UNIT_PRICE QUANTITY 334 1 26 48.75 1 334 2 46 39.16 4 334 3 12 10.48 4 335 1 32 5.65 2 336 1 2 29.55 5 336 2 20 28.21 5 337 1 32 5.65 4 337 2 29 24.71 4 337 3 45 31.68 3 338 1 35 7.18 2 338 2 13 12.64 5 339 1 38 22.98 3 339 2 13 12.64 3 340 1 41 8.66 3 340 2 26 48.75 5 340 3 27 39.91 2 341 1 12 10.48 4 341 2 43 16.64 1 342 1 30 37.34 1 342 2 44 39.32 4 343 1 3 16.67 1 343 2 14 26.14 3 343 3 2 29.55 4 344 1 17 39.89 3 344 2 23 10.33 4 345 1 14 26.14 1 346 1 2 29.55 5 346 2 26 48.75 3 347 1 35 7.18 5 347 2 41 8.66 1 348 1 2 29.55 4 348 2 21 38.34 5 349 1 11 30.69 5 349 2 12 10.48 4 350 1 33 37.0 2 350 2 32 5.65 1 351 1 23 10.33 4 351 2 29 24.71 4 352 1 46 39.16 2 352 2 22 39.78 5 352 3 35 7.18 2 353 1 28 10.24 4 354 1 44 39.32 4 354 2 42 10.11 3 355 1 34 23.32 2 355 2 27 39.91 4 356 1 8 19.58 3 356 2 38 22.98 5 357 1 42 10.11 4 357 2 20 28.21 4 358 1 12 10.48 3 359 1 10 29.49 5 359 2 9 21.16 3 360 1 39 11.0 2 361 1 19 14.34 3 362 1 5 43.71 5 362 2 7 19.16 3 363 1 21 38.34 3 364 1 20 28.21 4 364 2 27 39.91 3 364 3 13 12.64 3 365 1 4 44.17 3 365 2 43 16.64 4 366 1 36 49.12 4 366 2 42 10.11 4 366 3 29 24.71 4 367 1 7 19.16 2 368 1 27 39.91 4 368 2 19 14.34 5 369 1 44 39.32 5 369 2 22 39.78 2 370 1 25 9.8 4 370 2 21 38.34 5 371 1 7 19.16 4 371 2 28 10.24 4 371 3 41 8.66 2 372 1 17 39.89 2 373 1 23 10.33 5 373 2 32 5.65 2 373 3 19 14.34 4 374 1 20 28.21 1 374 2 29 24.71 4 375 1 31 28.59 4 375 2 22 39.78 2 376 1 15 13.97 1 376 2 43 16.64 5 377 1 21 38.34 4 377 2 11 30.69 2 378 1 15 13.97 4 378 2 27 39.91 4 379 1 39 11.0 4 379 2 12 10.48 5 380 1 7 19.16 3 380 2 42 10.11 3 381 1 10 29.49 3 381 2 20 28.21 4 382 1 5 43.71 4 382 2 38 22.98 3 383 1 26 48.75 5 383 2 8 19.58 4 384 1 26 48.75 3 384 2 36 49.12 1 385 1 21 38.34 3 385 2 41 8.66 4 386 1 14 26.14 5 386 2 42 10.11 2 387 1 37 29.51 4 387 2 41 8.66 1 387 3 36 49.12 4 388 1 11 30.69 3 388 2 9 21.16 5 389 1 23 10.33 2 390 1 29 24.71 3 390 2 5 43.71 4 390 3 15 13.97 4 391 1 43 16.64 1 391 2 38 22.98 5 392 1 24 48.39 1 392 2 45 31.68 1 392 3 8 19.58 3 393 1 24 48.39 3 394 1 19 14.34 4 394 2 32 5.65 3 395 1 27 39.91 2 395 2 44 39.32 4 395 3 29 24.71 4 396 1 30 37.34 2 396 2 19 14.34 1 396 3 42 10.11 2 397 1 43 16.64 4 397 2 33 37.0 5 398 1 24 48.39 3 398 2 13 12.64 3 398 3 25 9.8 1 399 1 26 48.75 3 399 2 16 13.09 3 399 3 10 29.49 5 400 1 44 39.32 4 400 2 10 29.49 4 401 1 28 10.24 3 401 2 12 10.48 2 402 1 10 29.49 2 402 2 22 39.78 3 402 3 37 29.51 4 403 1 41 8.66 3 403 2 34 23.32 2 403 3 28 10.24 5 404 1 37 29.51 2 404 2 5 43.71 4 405 1 46 27.64 1 406 1 43 16.64 3 407 1 27 39.91 3 407 2 11 30.69 4 408 1 42 10.11 1 409 1 21 38.34 4 409 2 19 14.34 1 410 1 16 13.09 5 410 2 23 10.33 3 411 1 30 37.34 4 411 2 18 24.46 2 412 1 39 11.0 1 412 2 35 7.18 4 412 3 10 29.49 5 413 1 8 19.58 3 413 2 24 48.39 4 414 1 16 13.09 2 414 2 38 22.98 1 415 1 29 24.71 5 415 2 42 10.11 4 416 1 8 19.58 3 416 2 24 48.39 1 417 1 13 12.64 3 417 2 46 27.64 2 417 3 43 16.64 4 418 1 36 49.12 4 418 2 43 16.64 2 419 1 9 21.16 3 419 2 16 13.09 2 420 1 3 16.67 4 420 2 33 37.0 5 420 3 13 12.64 3 421 1 43 16.64 1 422 1 46 39.16 5 423 1 23 10.33 5 423 2 6 38.28 3 424 1 29 24.71 4 424 2 32 5.65 3 425 1 13 12.64 4 425 2 35 7.18 3 426 1 30 37.34 5 426 2 38 22.98 2 427 1 28 10.24 5 427 2 18 24.46 2 428 1 13 12.64 4 429 1 21 38.34 5 429 2 46 39.16 5 430 1 18 24.46 2 430 2 15 13.97 5 431 1 23 10.33 5 431 2 11 30.69 5 431 3 14 26.14 2 432 1 42 10.11 2 432 2 16 13.09 3 433 1 19 14.34 5 433 2 29 24.71 2 434 1 28 10.24 5 434 2 30 37.34 5 434 3 2 29.55 4 435 1 16 13.09 1 435 2 43 16.64 4 435 3 34 23.32 3 436 1 14 26.14 5 436 2 37 29.51 4 437 1 37 29.51 3 437 2 20 28.21 5 438 1 33 37.0 3 438 2 32 5.65 5 438 3 30 37.34 2 439 1 32 5.65 5 439 2 44 39.32 1 440 1 23 10.33 3 440 2 15 13.97 2 441 1 38 22.98 2 441 2 11 30.69 3 442 1 46 27.64 2 442 2 25 9.8 4 443 1 46 39.16 4 444 1 45 31.68 2 444 2 42 10.11 1 445 1 34 23.32 3 445 2 10 29.49 2 445 3 46 39.16 4 446 1 37 29.51 3 446 2 24 48.39 2 447 1 38 22.98 2 447 2 36 

In [0]:
# selecting only the required columns and assigning this back to the order_items variable
order_items = order_items.drop('LINE_ITEM_ID')

In [0]:
# revieiwing the order_items dataframe
order_items.display()

ORDER_ID PRODUCT_ID UNIT_PRICE QUANTITY 334 26 48.75 1 334 46 39.16 4 334 12 10.48 4 335 32 5.65 2 336 2 29.55 5 336 20 28.21 5 337 32 5.65 4 337 29 24.71 4 337 45 31.68 3 338 35 7.18 2 338 13 12.64 5 339 38 22.98 3 339 13 12.64 3 340 41 8.66 3 340 26 48.75 5 340 27 39.91 2 341 12 10.48 4 341 43 16.64 1 342 30 37.34 1 342 44 39.32 4 343 3 16.67 1 343 14 26.14 3 343 2 29.55 4 344 17 39.89 3 344 23 10.33 4 345 14 26.14 1 346 2 29.55 5 346 26 48.75 3 347 35 7.18 5 347 41 8.66 1 348 2 29.55 4 348 21 38.34 5 349 11 30.69 5 349 12 10.48 4 350 33 37.0 2 350 32 5.65 1 351 23 10.33 4 351 29 24.71 4 352 46 39.16 2 352 22 39.78 5 352 35 7.18 2 353 28 10.24 4 354 44 39.32 4 354 42 10.11 3 355 34 23.32 2 355 27 39.91 4 356 8 19.58 3 356 38 22.98 5 357 42 10.11 4 357 20 28.21 4 358 12 10.48 3 359 10 29.49 5 359 9 21.16 3 360 39 11.0 2 361 19 14.34 3 362 5 43.71 5 362 7 19.16 3 363 21 38.34 3 364 20 28.21 4 364 27 39.91 3 364 13 12.64 3 365 4 44.17 3 365 43 16.64 4 366 36 49.12 4 366 42 10.11 4 366 29 24.71 4 367 7 19.16 2 368 27 39.91 4 368 19 14.34 5 369 44 39.32 5 369 22 39.78 2 370 25 9.8 4 370 21 38.34 5 371 7 19.16 4 371 28 10.24 4 371 41 8.66 2 372 17 39.89 2 373 23 10.33 5 373 32 5.65 2 373 19 14.34 4 374 20 28.21 1 374 29 24.71 4 375 31 28.59 4 375 22 39.78 2 376 15 13.97 1 376 43 16.64 5 377 21 38.34 4 377 11 30.69 2 378 15 13.97 4 378 27 39.91 4 379 39 11.0 4 379 12 10.48 5 380 7 19.16 3 380 42 10.11 3 381 10 29.49 3 381 20 28.21 4 382 5 43.71 4 382 38 22.98 3 383 26 48.75 5 383 8 19.58 4 384 26 48.75 3 384 36 49.12 1 385 21 38.34 3 385 41 8.66 4 386 14 26.14 5 386 42 10.11 2 387 37 29.51 4 387 41 8.66 1 387 36 49.12 4 388 11 30.69 3 388 9 21.16 5 389 23 10.33 2 390 29 24.71 3 390 5 43.71 4 390 15 13.97 4 391 43 16.64 1 391 38 22.98 5 392 24 48.39 1 392 45 31.68 1 392 8 19.58 3 393 24 48.39 3 394 19 14.34 4 394 32 5.65 3 395 27 39.91 2 395 44 39.32 4 395 29 24.71 4 396 30 37.34 2 396 19 14.34 1 396 42 10.11 2 397 43 16.64 4 397 33 37.0 5 398 24 48.39 3 398 13 12.64 3 398 25 9.8 1 399 26 48.75 3 399 16 13.09 3 399 10 29.49 5 400 44 39.32 4 400 10 29.49 4 401 28 10.24 3 401 12 10.48 2 402 10 29.49 2 402 22 39.78 3 402 37 29.51 4 403 41 8.66 3 403 34 23.32 2 403 28 10.24 5 404 37 29.51 2 404 5 43.71 4 405 46 27.64 1 406 43 16.64 3 407 27 39.91 3 407 11 30.69 4 408 42 10.11 1 409 21 38.34 4 409 19 14.34 1 410 16 13.09 5 410 23 10.33 3 411 30 37.34 4 411 18 24.46 2 412 39 11.0 1 412 35 7.18 4 412 10 29.49 5 413 8 19.58 3 413 24 48.39 4 414 16 13.09 2 414 38 22.98 1 415 29 24.71 5 415 42 10.11 4 416 8 19.58 3 416 24 48.39 1 417 13 12.64 3 417 46 27.64 2 417 43 16.64 4 418 36 49.12 4 418 43 16.64 2 419 9 21.16 3 419 16 13.09 2 420 3 16.67 4 420 33 37.0 5 420 13 12.64 3 421 43 16.64 1 422 46 39.16 5 423 23 10.33 5 423 6 38.28 3 424 29 24.71 4 424 32 5.65 3 425 13 12.64 4 425 35 7.18 3 426 30 37.34 5 426 38 22.98 2 427 28 10.24 5 427 18 24.46 2 428 13 12.64 4 429 21 38.34 5 429 46 39.16 5 430 18 24.46 2 430 15 13.97 5 431 23 10.33 5 431 11 30.69 5 431 14 26.14 2 432 42 10.11 2 432 16 13.09 3 433 19 14.34 5 433 29 24.71 2 434 28 10.24 5 434 30 37.34 5 434 2 29.55 4 435 16 13.09 1 435 43 16.64 4 435 34 23.32 3 436 14 26.14 5 436 37 29.51 4 437 37 29.51 3 437 20 28.21 5 438 33 37.0 3 438 32 5.65 5 438 30 37.34 2 439 32 5.65 5 439 44 39.32 1 440 23 10.33 3 440 15 13.97 2 441 38 22.98 2 441 11 30.69 3 442 46 27.64 2 442 25 9.8 4 443 46 39.16 4 444 45 31.68 2 444 42 10.11 1 445 34 23.32 3 445 10 29.49 2 445 46 39.16 4 446 37 29.51 3 446 24 48.39 2 447 38 22.98 2 447 36 49.12 4 448 32 5.65 2 449 45 31.68 4 449 21 38.34 4 449 20 28.21 4 450 33 37.0 2 451 28 10.24 4 452 29 24.71 3 452 43 16.64 2 452 36 49.12 2 453 43 16.64 3 453 2 29.55 2 454 41 8.66 4 454 27 39.91 3 455 7 19.16 2 455 29 24.71 3 455 23 10.33 4 456 6 38.28 5 456 46 39.16 4 457 46 39.16 1 458 38 22.98 2 458 14 26.14 2 459 38 22.98 4 460 5 43.71 3 460 32 5.65 3 461 40 34.06 4 461 26 48.75 4 462 19 14.34 1 462 16 13.09 3 463 34 23.32 4 463 29 24.71 3 464 44 39.32 5 465 11 30.69 5 466 4

In [0]:
# writing the order_items parquet table in the silver layer
order_items.write.parquet("/mnt/silver/order_items", mode='overwrite')

#### PRODUCTS

Save a table called PRODUCTS in the silver layer, it should contain the following columns:
- PRODUCT_ID, type INTEGER
- PRODUCT_NAME, type STRING
- UNIT_PRICE, type DOUBLE

The file should be saved in PARQUET format.

In [0]:
# Reading the products csv file

products_path = "/mnt/bronze/products.csv"

products_schema = StructType([
                    StructField("PRODUCT_ID", IntegerType(), False),
                    StructField("PRODUCT_NAME", StringType(), False),
                    StructField("UNIT_PRICE", DoubleType(), False)
                    ]
                    )

products=spark.read.csv(path=products_path, header=True, schema=products_schema)

In [0]:
# reviewing the records
products.display()

PRODUCT_ID PRODUCT_NAME UNIT_PRICE 16 Women's Socks (Grey) 39.89 17 Women's Sweater (Brown) 24.46 18 Women's Jacket (Black) 14.34 19 Men's Coat (Red) 28.21 20 Girl's Shorts (Green) 38.34 21 Girl's Pyjamas (White) 39.78 22 Men's Shorts (Black) 10.33 23 Men's Pyjamas (Blue) 48.39 24 Boy's Sweater (Red) 9.8 25 Girl's Jeans (Grey) 48.75 26 Girl's Hoodie (White) 39.91 27 Boy's Coat (Blue) 10.24 28 Men's Hoodie (Red) 24.71 29 Boy's Shirt (Black) 37.34 30 Women's Pyjamas (Grey) 28.59 31 Women's Skirt (Green) 5.65 32 Women's Jacket (Blue) 37.0 33 Boy's Pyjamas (Grey) 23.32 34 Women's Jeans (Red) 7.18 35 Girl's Dress (Red) 49.12 36 Women's Trousers (Blue) 29.51 37 Boy's Jeans (Blue) 22.98 38 Girl's Pyjamas (Red) 11.0 39 Boy's Trousers (Blue) 34.06 40 Girl's Pyjamas (Black) 8.66 41 Women's Dress (Black) 10.11 1 Boy's Shirt (White) 29.55 2 Women's Shirt (Green) 16.67 3 Boy's Sweater (Green) 44.17 4 Boy's Trousers (White) 43.71 5 Girl's Shorts (Red) 38.28 6 Boy's Socks (Grey) 19.16 7 Boy's Socks (Black) 19.58 8 Boy's Coat (Brown) 21.16 9 Women's Jeans (Brown) 29.49 10 Women's Skirt (Red) 30.69 11 Boy's Shorts (Blue) 10.48 12 Boy's Socks (White) 12.64 13 Boy's Hoodie (Grey) 26.14 14 Women's Skirt (Brown) 13.97 15 Girl's Coat (Blue) 13.09 42 Boy's Jeans (Black) 16.64 43 Boy's Trousers (Black) 39.32 44 Women's Coat (Black) 31.68 45 Men's Jeans (Grey) 27.64 46 Girl's Trousers (Red) 39.16

In [0]:
# writing the parquet file
products.write.parquet('/mnt/silver/products', mode='overwrite')

#### CUSTOMERS

Save a table called CUSTOMERS in the silver layer, it should contain the following columns:
- CUSTOMER_ID, type INTEGER
- FULL_NAME, type STRING
- EMAIL_ADDRESS, type STRING

The file should be saved in PARQUET format.

In [0]:
# Reading the customers csv file
customers_path = "/mnt/bronze/customers.csv"

customers_schema = StructType([
                    StructField("CUSTOMER_ID", IntegerType(), False),
                    StructField("FULL_NAME", StringType(), False),
                    StructField("EMAIL_ADDRESS", StringType(), False)
                    ]
                    )

customers=spark.read.csv(path=customers_path, header=True, schema=customers_schema)

In [0]:
# reviewing the dataframe
customers.display()

CUSTOMER_ID FULL_NAME EMAIL_ADDRESS 286 Wilfred Welch wilfred.welch@internalmail 287 Kristina Nunez kristina.nunez@internalmail 288 Mable Ballard mable.ballard@internalmail 289 Diane Wilkerson diane.wilkerson@internalmail 290 Sheryl Banks sheryl.banks@internalmail 291 Opal Cruz opal.cruz@internalmail 292 Dale Hughes dale.hughes@internalmail 293 Diana Fowler diana.fowler@internalmail 294 Travis Schwartz travis.schwartz@internalmail 295 Anthony Boone anthony.boone@internalmail 296 Tim Harmon tim.harmon@internalmail 297 Kristin Brooks kristin.brooks@internalmail 298 Kathy Dennis kathy.dennis@internalmail 299 Vickie James vickie.james@internalmail 300 Sandra Bass sandra.bass@internalmail 301 Nelson Tate nelson.tate@internalmail 302 Tiffany Pena tiffany.pena@internalmail 303 Jeannette Hunt jeannette.hunt@internalmail 304 Willie Cunningham willie.cunningham@internalmail 305 Paulette Byrd paulette.byrd@internalmail 306 Tasha Cobb tasha.cobb@internalmail 307 Eloise Burton eloise.burton@internalmail 308 Felix Fox felix.fox@internalmail 309 Gary Barton gary.barton@internalmail 310 Tracy Mcbride tracy.mcbride@internalmail 311 Lorita Koenig lorita.koenig@internalmail 312 Kaleigh Meade kaleigh.meade@internalmail 313 Lexie Magee lexie.magee@internalmail 314 Landon Neville landon.neville@internalmail 315 Lillia Talbott lillia.talbott@internalmail 316 Dinah Paredes dinah.paredes@internalmail 317 Mercy Whiting mercy.whiting@internalmail 318 Thomas Huddleston thomas.huddleston@internalmail 319 Rubi Carlisle rubi.carlisle@internalmail 320 Vivien Cameron vivien.cameron@internalmail 321 Maia Leggett maia.leggett@internalmail 322 Florencia Kohler florencia.kohler@internalmail 323 Lucila Heck lucila.heck@internalmail 324 Kendrick Caraballo kendrick.caraballo@internalmail 325 Annemarie Pinckney annemarie.pinckney@internalmail 326 Carmella Avalos carmella.avalos@internalmail 327 Jules Ruffin jules.ruffin@internalmail 328 Tish Stapleton tish.stapleton@internalmail 329 Elin Seidel elin.seidel@internalmail 330 Shawn Sorenson shawn.sorenson@internalmail 331 Winfred August winfred.august@internalmail 332 Virgie Breeden virgie.breeden@internalmail 333 Ericka Oconner ericka.oconner@internalmail 334 Cheree Kemp cheree.kemp@internalmail 335 Rayford Salley rayford.salley@internalmail 336 Zulma Olds zulma.olds@internalmail 337 Salena Wadsworth salena.wadsworth@internalmail 338 Mohammad Cervantes mohammad.cervantes@internalmail 339 Tanja Vanover tanja.vanover@internalmail 340 Lonnie Colby lonnie.colby@internalmail 341 Monte Calloway monte.calloway@internalmail 342 Melisa Banda melisa.banda@internalmail 343 Gisela Costello gisela.costello@internalmail 344 Libby Krauss libby.krauss@internalmail 345 Mireille Pauley mireille.pauley@internalmail 346 Hassie Grogan hassie.grogan@internalmail 347 Chi Mcwhorter chi.mcwhorter@internalmail 348 Connie Delagarza connie.delagarza@internalmail 349 Britney Gable britney.gable@internalmail 350 Lorilee Bautista lorilee.bautista@internalmail 351 Anisa Kurtz anisa.kurtz@internalmail 352 Maryalice Evers maryalice.evers@internalmail 353 Andria Myles andria.myles@internalmail 354 Dede Bundy dede.bundy@internalmail 355 Twila Hilliard twila.hilliard@internalmail 356 Gene Mcginnis gene.mcginnis@internalmail 357 Shaquana Carney shaquana.carney@internalmail 358 Gita Dobbs gita.dobbs@internalmail 359 Dorathy Hutchings dorathy.hutchings@internalmail 360 Shirley Ward shirley.ward@internalmail 361 Frank Perez frank.perez@internalmail 362 Barbara Allen barbara.allen@internalmail 363 Justin King justin.king@internalmail 364 Harold Griffin harold.griffin@internalmail 365 Jeffrey Coleman jeffrey.coleman@internalmail 366 Margaret Bennett margaret.bennett@internalmail 367 Cheryl Phillips cheryl.phillips@internalmail 368 Joan Miller joan.miller@internalmail 369 Chris Powell chris.powell@internalmail 370 Russell Rivera russell.rivera@internalmail 371 Nancy Hall nancy.hall@internalmail 372 Gerald Evans gerald.evans@internalmail 373 Jennifer Cooper jenni

In [0]:
# writing the parquet file
customers.write.parquet('/mnt/silver/customers', mode='overwrite')

# Silver to Gold


#### ORDER_DETAILS

Create an order_details table that contains the following attributes:

- ORDER ID
- ORDER DATE
- CUSTOMER ID
- STORE NAME
- TOTAL ORDER AMOUNT 

The table should be aggregated by ORDER ID, ORDER DATE, CUSTOMER ID and STORE NAME to show the TOTAL ORDER AMOUNT.

Hint: Please consider the order of operations when finding the TOTAL ORDER AMOUNT.

In [0]:
# import the functions and read silver data tables as DataFrames
from pyspark.sql.functions import *

orders = spark.read.parquet('/mnt/silver/orders')
order_items = spark.read.parquet('/mnt/silver/order_items')
products = spark.read.parquet('/mnt/silver/products')
customers = spark.read.parquet('/mnt/silver/customers')

In [0]:
# display the orders dataframe to review the columns
orders.display()

ORDER_ID ORDER_TIMESTAMP CUSTOMER_ID STORE_NAME 447 2022-01-06T09:35:42Z 355 Online 448 2022-01-06T10:23:14Z 155 Online 449 2022-01-06T01:21:54Z 242 Online 450 2022-01-06T05:57:04Z 49 Online 451 2022-01-06T10:39:07Z 204 Online 452 2022-01-07T01:11:46Z 216 Online 453 2022-01-07T06:53:06Z 4 New York City 454 2022-01-07T03:55:15Z 388 Online 455 2022-01-07T06:38:38Z 291 Online 456 2022-01-08T12:52:12Z 272 Online 457 2022-01-08T10:13:30Z 307 Online 458 2022-01-08T11:03:34Z 42 Online 459 2022-01-09T02:35:19Z 390 Online 460 2022-01-09T03:35:53Z 235 Online 461 2022-01-09T12:54:10Z 302 Online 462 2022-01-09T02:44:45Z 357 Online 463 2022-01-09T02:54:31Z 271 Online 464 2022-01-09T05:16:13Z 79 Online 465 2022-01-09T09:42:53Z 280 Online 466 2022-01-10T07:42:04Z 210 Bucharest 467 2022-01-11T01:25:06Z 293 Online 469 2022-01-12T10:22:10Z 239 Online 470 2022-01-12T11:40:14Z 217 Online 471 2022-01-12T12:02:56Z 61 Seattle 472 2022-01-12T12:40:49Z 182 Online 473 2022-01-12T01:24:18Z 116 Online 474 2022-01-12T06:17:28Z 244 Online 475 2022-01-12T10:20:52Z 210 Online 476 2022-01-12T10:41:43Z 84 Online 477 2022-01-13T01:00:02Z 374 Online 478 2022-01-13T06:17:28Z 389 Online 479 2022-01-13T07:13:56Z 368 Online 480 2022-01-13T08:44:34Z 344 Online 481 2022-01-13T11:40:21Z 118 Online 482 2022-01-13T01:54:39Z 88 Online 483 2022-01-13T09:10:36Z 72 Online 484 2022-01-14T04:30:58Z 159 Online 485 2022-01-15T05:21:41Z 134 Online 486 2022-01-15T01:27:37Z 105 Online 487 2022-01-15T02:04:27Z 259 Online 488 2022-01-15T06:29:22Z 150 Online 490 2022-01-16T02:18:47Z 48 Online 491 2022-01-16T11:36:07Z 264 Seattle 492 2022-01-16T08:30:25Z 381 Online 493 2022-01-17T06:17:22Z 155 Online 494 2022-01-17T09:41:15Z 256 Online 495 2022-01-17T06:07:00Z 205 San Francisco 496 2022-01-17T11:58:50Z 33 New York City 497 2022-01-18T12:59:01Z 164 Online 498 2022-01-18T03:48:04Z 262 Online 499 2022-01-18T02:11:23Z 333 Online 500 2022-01-18T03:56:55Z 200 Online 501 2022-01-18T10:14:50Z 367 Online 502 2022-01-19T02:50:53Z 355 Online 503 2022-01-20T06:55:43Z 243 Online 504 2022-01-21T06:03:09Z 107 Online 505 2022-01-22T02:08:42Z 248 Online 506 2022-01-22T05:36:47Z 4 Online 507 2022-01-22T10:43:04Z 137 Online 508 2022-01-22T02:47:09Z 157 Online 509 2022-01-22T04:07:52Z 303 Online 510 2022-01-22T11:53:07Z 322 Online 511 2022-01-23T02:08:50Z 22 Online 512 2022-01-23T09:07:16Z 235 Seattle 513 2022-01-24T02:40:25Z 15 Online 514 2022-01-24T05:30:03Z 63 Online 515 2022-01-24T03:30:17Z 385 Online 516 2022-01-24T05:11:24Z 30 Online 517 2022-01-24T08:54:50Z 302 Online 518 2022-01-25T07:01:14Z 125 Online 519 2022-01-25T11:02:55Z 207 Online 520 2022-01-25T11:27:33Z 35 London 521 2022-01-26T03:32:49Z 157 Online 522 2022-01-26T06:10:38Z 298 Online 523 2022-01-26T11:33:09Z 60 Online 524 2022-01-26T12:48:31Z 287 Online 525 2022-01-26T05:01:17Z 43 Online 527 2022-01-27T04:36:29Z 272 Online 528 2022-01-27T06:57:51Z 143 Online 529 2022-01-27T07:48:59Z 253 Online 530 2022-01-27T08:18:37Z 311 Online 531 2022-01-27T12:50:09Z 237 Online 532 2022-01-28T08:05:40Z 251 Online 533 2022-01-28T12:55:59Z 130 Online 534 2022-01-28T03:08:46Z 362 Online 535 2022-01-29T12:06:37Z 319 Online 536 2022-01-29T07:57:30Z 370 Online 537 2022-01-29T01:36:37Z 49 Online 538 2022-01-30T04:05:58Z 385 Online 540 2022-01-30T11:09:41Z 41 Online 541 2022-01-30T02:15:41Z 173 Online 542 2022-01-31T01:01:48Z 216 Online 543 2022-01-31T02:09:48Z 357 Utrecht 544 2022-01-31T01:12:13Z 3 Online 545 2022-01-31T02:23:17Z 35 Online 546 2022-01-31T03:15:43Z 60 San Francisco 547 2022-02-01T02:49:11Z 72 Online 548 2022-02-01T11:35:24Z 140 Online 549 2022-02-01T12:43:49Z 385 Berlin 550 2022-02-01T02:42:29Z 313 Online 551 2022-02-01T06:59:51Z 190 Online 552 2022-02-02T01:42:52Z 209 London 553 2022-02-02T10:21:55Z 35 Online 554 2022-02-02T10:51:55Z 93 Online 555 2022-02-02T01:30:47Z 105 Online 556 2022-02-02T06:06:57Z 143 Online 557 2022-02-02T07:26:21Z 221 Online 558 2022-02-02T10:49:37Z 206 Seattle 559 2022-02-03T02:56:32Z 38 Online 560 2022-02-03T06:13:1

In [0]:
# datatype of the order_timestamp column is timestamp and needs to be changed to date
orders.dtypes

[('ORDER_ID', 'int'),
 ('ORDER_TIMESTAMP', 'timestamp'),
 ('CUSTOMER_ID', 'int'),
 ('STORE_NAME', 'string')]

In [0]:
# changing the order_timestamp from 'timestamp' to 'date' using the to_date function
# assigning the result to the order_details dataframe
order_details = orders.select(
'ORDER_ID',
to_date('order_timestamp').alias('DATE'),
'CUSTOMER_ID',
'STORE_NAME'
)

In [0]:
# reviewing the current state of the order details dataframe
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME 447 2022-01-06 355 Online 448 2022-01-06 155 Online 449 2022-01-06 242 Online 450 2022-01-06 49 Online 451 2022-01-06 204 Online 452 2022-01-07 216 Online 453 2022-01-07 4 New York City 454 2022-01-07 388 Online 455 2022-01-07 291 Online 456 2022-01-08 272 Online 457 2022-01-08 307 Online 458 2022-01-08 42 Online 459 2022-01-09 390 Online 460 2022-01-09 235 Online 461 2022-01-09 302 Online 462 2022-01-09 357 Online 463 2022-01-09 271 Online 464 2022-01-09 79 Online 465 2022-01-09 280 Online 466 2022-01-10 210 Bucharest 467 2022-01-11 293 Online 469 2022-01-12 239 Online 470 2022-01-12 217 Online 471 2022-01-12 61 Seattle 472 2022-01-12 182 Online 473 2022-01-12 116 Online 474 2022-01-12 244 Online 475 2022-01-12 210 Online 476 2022-01-12 84 Online 477 2022-01-13 374 Online 478 2022-01-13 389 Online 479 2022-01-13 368 Online 480 2022-01-13 344 Online 481 2022-01-13 118 Online 482 2022-01-13 88 Online 483 2022-01-13 72 Online 484 2022-01-14 159 Online 485 2022-01-15 134 Online 486 2022-01-15 105 Online 487 2022-01-15 259 Online 488 2022-01-15 150 Online 490 2022-01-16 48 Online 491 2022-01-16 264 Seattle 492 2022-01-16 381 Online 493 2022-01-17 155 Online 494 2022-01-17 256 Online 495 2022-01-17 205 San Francisco 496 2022-01-17 33 New York City 497 2022-01-18 164 Online 498 2022-01-18 262 Online 499 2022-01-18 333 Online 500 2022-01-18 200 Online 501 2022-01-18 367 Online 502 2022-01-19 355 Online 503 2022-01-20 243 Online 504 2022-01-21 107 Online 505 2022-01-22 248 Online 506 2022-01-22 4 Online 507 2022-01-22 137 Online 508 2022-01-22 157 Online 509 2022-01-22 303 Online 510 2022-01-22 322 Online 511 2022-01-23 22 Online 512 2022-01-23 235 Seattle 513 2022-01-24 15 Online 514 2022-01-24 63 Online 515 2022-01-24 385 Online 516 2022-01-24 30 Online 517 2022-01-24 302 Online 518 2022-01-25 125 Online 519 2022-01-25 207 Online 520 2022-01-25 35 London 521 2022-01-26 157 Online 522 2022-01-26 298 Online 523 2022-01-26 60 Online 524 2022-01-26 287 Online 525 2022-01-26 43 Online 527 2022-01-27 272 Online 528 2022-01-27 143 Online 529 2022-01-27 253 Online 530 2022-01-27 311 Online 531 2022-01-27 237 Online 532 2022-01-28 251 Online 533 2022-01-28 130 Online 534 2022-01-28 362 Online 535 2022-01-29 319 Online 536 2022-01-29 370 Online 537 2022-01-29 49 Online 538 2022-01-30 385 Online 540 2022-01-30 41 Online 541 2022-01-30 173 Online 542 2022-01-31 216 Online 543 2022-01-31 357 Utrecht 544 2022-01-31 3 Online 545 2022-01-31 35 Online 546 2022-01-31 60 San Francisco 547 2022-02-01 72 Online 548 2022-02-01 140 Online 549 2022-02-01 385 Berlin 550 2022-02-01 313 Online 551 2022-02-01 190 Online 552 2022-02-02 209 London 553 2022-02-02 35 Online 554 2022-02-02 93 Online 555 2022-02-02 105 Online 556 2022-02-02 143 Online 557 2022-02-02 221 Online 558 2022-02-02 206 Seattle 559 2022-02-03 38 Online 560 2022-02-03 235 Online 561 2022-02-03 38 Online 562 2022-02-04 87 Online 563 2022-02-04 213 Online 564 2022-02-04 30 Online 565 2022-02-04 385 Online 566 2022-02-05 317 Online 567 2022-02-05 391 Online 568 2022-02-05 97 Online 569 2022-02-05 291 Online 570 2022-02-05 343 Online 571 2022-02-05 273 Online 572 2022-02-06 368 Online 573 2022-02-06 41 Online 574 2022-02-07 101 Online 575 2022-02-08 118 Online 577 2022-02-08 65 Online 578 2022-02-08 218 Online 579 2022-02-08 121 Chicago 580 2022-02-08 235 Online 581 2022-02-08 41 Online 582 2022-02-09 215 Online 583 2022-02-09 205 Online 584 2022-02-10 67 Utrecht 585 2022-02-10 4 Online 586 2022-02-10 131 Online 587 2022-02-10 82 Online 588 2022-02-10 110 Online 589 2022-02-11 284 Online 590 2022-02-11 60 Online 591 2022-02-11 35 London 592 2022-02-11 123 Online 593 2022-02-12 152 Online 594 2022-02-12 358 Online 595 2022-02-12 378 Online 596 2022-02-13 357 Utrecht 597 2022-02-13 269 Online 598 2022-02-14 203 Online 599 2022-02-14 43 Online 600 2022-02-14 147 San Francisco 602 2022-02-14 24 Online 603 2022-02-15 260 Online 604 2022-02-15 346 Online 605 2022-0

In [0]:
# reviewing the columns of the order_items dataframe
order_items.display()

ORDER_ID PRODUCT_ID UNIT_PRICE QUANTITY 334 26 48.75 1 334 46 39.16 4 334 12 10.48 4 335 32 5.65 2 336 2 29.55 5 336 20 28.21 5 337 32 5.65 4 337 29 24.71 4 337 45 31.68 3 338 35 7.18 2 338 13 12.64 5 339 38 22.98 3 339 13 12.64 3 340 41 8.66 3 340 26 48.75 5 340 27 39.91 2 341 12 10.48 4 341 43 16.64 1 342 30 37.34 1 342 44 39.32 4 343 3 16.67 1 343 14 26.14 3 343 2 29.55 4 344 17 39.89 3 344 23 10.33 4 345 14 26.14 1 346 2 29.55 5 346 26 48.75 3 347 35 7.18 5 347 41 8.66 1 348 2 29.55 4 348 21 38.34 5 349 11 30.69 5 349 12 10.48 4 350 33 37.0 2 350 32 5.65 1 351 23 10.33 4 351 29 24.71 4 352 46 39.16 2 352 22 39.78 5 352 35 7.18 2 353 28 10.24 4 354 44 39.32 4 354 42 10.11 3 355 34 23.32 2 355 27 39.91 4 356 8 19.58 3 356 38 22.98 5 357 42 10.11 4 357 20 28.21 4 358 12 10.48 3 359 10 29.49 5 359 9 21.16 3 360 39 11.0 2 361 19 14.34 3 362 5 43.71 5 362 7 19.16 3 363 21 38.34 3 364 20 28.21 4 364 27 39.91 3 364 13 12.64 3 365 4 44.17 3 365 43 16.64 4 366 36 49.12 4 366 42 10.11 4 366 29 24.71 4 367 7 19.16 2 368 27 39.91 4 368 19 14.34 5 369 44 39.32 5 369 22 39.78 2 370 25 9.8 4 370 21 38.34 5 371 7 19.16 4 371 28 10.24 4 371 41 8.66 2 372 17 39.89 2 373 23 10.33 5 373 32 5.65 2 373 19 14.34 4 374 20 28.21 1 374 29 24.71 4 375 31 28.59 4 375 22 39.78 2 376 15 13.97 1 376 43 16.64 5 377 21 38.34 4 377 11 30.69 2 378 15 13.97 4 378 27 39.91 4 379 39 11.0 4 379 12 10.48 5 380 7 19.16 3 380 42 10.11 3 381 10 29.49 3 381 20 28.21 4 382 5 43.71 4 382 38 22.98 3 383 26 48.75 5 383 8 19.58 4 384 26 48.75 3 384 36 49.12 1 385 21 38.34 3 385 41 8.66 4 386 14 26.14 5 386 42 10.11 2 387 37 29.51 4 387 41 8.66 1 387 36 49.12 4 388 11 30.69 3 388 9 21.16 5 389 23 10.33 2 390 29 24.71 3 390 5 43.71 4 390 15 13.97 4 391 43 16.64 1 391 38 22.98 5 392 24 48.39 1 392 45 31.68 1 392 8 19.58 3 393 24 48.39 3 394 19 14.34 4 394 32 5.65 3 395 27 39.91 2 395 44 39.32 4 395 29 24.71 4 396 30 37.34 2 396 19 14.34 1 396 42 10.11 2 397 43 16.64 4 397 33 37.0 5 398 24 48.39 3 398 13 12.64 3 398 25 9.8 1 399 26 48.75 3 399 16 13.09 3 399 10 29.49 5 400 44 39.32 4 400 10 29.49 4 401 28 10.24 3 401 12 10.48 2 402 10 29.49 2 402 22 39.78 3 402 37 29.51 4 403 41 8.66 3 403 34 23.32 2 403 28 10.24 5 404 37 29.51 2 404 5 43.71 4 405 46 27.64 1 406 43 16.64 3 407 27 39.91 3 407 11 30.69 4 408 42 10.11 1 409 21 38.34 4 409 19 14.34 1 410 16 13.09 5 410 23 10.33 3 411 30 37.34 4 411 18 24.46 2 412 39 11.0 1 412 35 7.18 4 412 10 29.49 5 413 8 19.58 3 413 24 48.39 4 414 16 13.09 2 414 38 22.98 1 415 29 24.71 5 415 42 10.11 4 416 8 19.58 3 416 24 48.39 1 417 13 12.64 3 417 46 27.64 2 417 43 16.64 4 418 36 49.12 4 418 43 16.64 2 419 9 21.16 3 419 16 13.09 2 420 3 16.67 4 420 33 37.0 5 420 13 12.64 3 421 43 16.64 1 422 46 39.16 5 423 23 10.33 5 423 6 38.28 3 424 29 24.71 4 424 32 5.65 3 425 13 12.64 4 425 35 7.18 3 426 30 37.34 5 426 38 22.98 2 427 28 10.24 5 427 18 24.46 2 428 13 12.64 4 429 21 38.34 5 429 46 39.16 5 430 18 24.46 2 430 15 13.97 5 431 23 10.33 5 431 11 30.69 5 431 14 26.14 2 432 42 10.11 2 432 16 13.09 3 433 19 14.34 5 433 29 24.71 2 434 28 10.24 5 434 30 37.34 5 434 2 29.55 4 435 16 13.09 1 435 43 16.64 4 435 34 23.32 3 436 14 26.14 5 436 37 29.51 4 437 37 29.51 3 437 20 28.21 5 438 33 37.0 3 438 32 5.65 5 438 30 37.34 2 439 32 5.65 5 439 44 39.32 1 440 23 10.33 3 440 15 13.97 2 441 38 22.98 2 441 11 30.69 3 442 46 27.64 2 442 25 9.8 4 443 46 39.16 4 444 45 31.68 2 444 42 10.11 1 445 34 23.32 3 445 10 29.49 2 445 46 39.16 4 446 37 29.51 3 446 24 48.39 2 447 38 22.98 2 447 36 49.12 4 448 32 5.65 2 449 45 31.68 4 449 21 38.34 4 449 20 28.21 4 450 33 37.0 2 451 28 10.24 4 452 29 24.71 3 452 43 16.64 2 452 36 49.12 2 453 43 16.64 3 453 2 29.55 2 454 41 8.66 4 454 27 39.91 3 455 7 19.16 2 455 29 24.71 3 455 23 10.33 4 456 6 38.28 5 456 46 39.16 4 457 46 39.16 1 458 38 22.98 2 458 14 26.14 2 459 38 22.98 4 460 5 43.71 3 460 32 5.65 3 461 40 34.06 4 461 26 48.75 4 462 19 14.34 1 462 16 13.09 3 463 34 23.32 4 463 29 24.71 3 464 44 39.32 5 465 11 30.69 5 466 4

In [0]:
# joining the order_details and order_items dataframe on the 'order_id' column of both tabes
# selecting the relevant columns from the resulting dataframs and storing it back to the order_details variable
order_details = order_details.join(order_items, order_items['order_id']==order_details['order_id'], 'left'). \
select(order_details['ORDER_ID'], order_details['DATE'], order_details['CUSTOMER_ID'], order_details['STORE_NAME'], order_items['UNIT_PRICE'], order_items['QUANTITY'])

In [0]:
# reviewing the current state of the order_details dataframe
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME UNIT_PRICE QUANTITY 447 2022-01-06 355 Online 49.12 4 447 2022-01-06 355 Online 22.98 2 448 2022-01-06 155 Online 5.65 2 449 2022-01-06 242 Online 28.21 4 449 2022-01-06 242 Online 38.34 4 449 2022-01-06 242 Online 31.68 4 450 2022-01-06 49 Online 37.0 2 451 2022-01-06 204 Online 10.24 4 452 2022-01-07 216 Online 49.12 2 452 2022-01-07 216 Online 16.64 2 452 2022-01-07 216 Online 24.71 3 453 2022-01-07 4 New York City 29.55 2 453 2022-01-07 4 New York City 16.64 3 454 2022-01-07 388 Online 39.91 3 454 2022-01-07 388 Online 8.66 4 455 2022-01-07 291 Online 10.33 4 455 2022-01-07 291 Online 24.71 3 455 2022-01-07 291 Online 19.16 2 456 2022-01-08 272 Online 39.16 4 456 2022-01-08 272 Online 38.28 5 457 2022-01-08 307 Online 39.16 1 458 2022-01-08 42 Online 26.14 2 458 2022-01-08 42 Online 22.98 2 459 2022-01-09 390 Online 22.98 4 460 2022-01-09 235 Online 5.65 3 460 2022-01-09 235 Online 43.71 3 461 2022-01-09 302 Online 48.75 4 461 2022-01-09 302 Online 34.06 4 462 2022-01-09 357 Online 13.09 3 462 2022-01-09 357 Online 14.34 1 463 2022-01-09 271 Online 24.71 3 463 2022-01-09 271 Online 23.32 4 464 2022-01-09 79 Online 39.32 5 465 2022-01-09 280 Online 30.69 5 466 2022-01-10 210 Bucharest 27.64 4 466 2022-01-10 210 Bucharest 8.66 5 467 2022-01-11 293 Online 44.17 3 469 2022-01-12 239 Online 39.78 1 469 2022-01-12 239 Online 31.68 4 470 2022-01-12 217 Online 16.64 5 470 2022-01-12 217 Online 16.67 5 471 2022-01-12 61 Seattle 39.78 2 472 2022-01-12 182 Online 37.0 1 473 2022-01-12 116 Online 27.64 3 473 2022-01-12 116 Online 8.66 4 474 2022-01-12 244 Online 7.18 4 474 2022-01-12 244 Online 30.69 2 475 2022-01-12 210 Online 24.46 3 475 2022-01-12 210 Online 23.32 3 475 2022-01-12 210 Online 29.55 5 476 2022-01-12 84 Online 39.16 5 476 2022-01-12 84 Online 13.09 5 477 2022-01-13 374 Online 29.49 1 477 2022-01-13 374 Online 29.51 3 478 2022-01-13 389 Online 39.32 3 478 2022-01-13 389 Online 30.69 4 478 2022-01-13 389 Online 10.33 3 479 2022-01-13 368 Online 19.16 3 479 2022-01-13 368 Online 31.68 1 480 2022-01-13 344 Online 19.16 4 481 2022-01-13 118 Online 49.12 4 481 2022-01-13 118 Online 21.16 1 481 2022-01-13 118 Online 10.48 5 482 2022-01-13 88 Online 31.68 2 482 2022-01-13 88 Online 39.78 2 482 2022-01-13 88 Online 7.18 4 483 2022-01-13 72 Online 14.34 4 484 2022-01-14 159 Online 10.24 4 484 2022-01-14 159 Online 8.66 3 485 2022-01-15 134 Online 29.49 4 485 2022-01-15 134 Online 12.64 3 486 2022-01-15 105 Online 44.17 1 486 2022-01-15 105 Online 8.66 3 487 2022-01-15 259 Online 39.89 2 488 2022-01-15 150 Online 37.34 3 488 2022-01-15 150 Online 13.09 4 490 2022-01-16 48 Online 29.49 1 491 2022-01-16 264 Seattle 10.11 4 491 2022-01-16 264 Seattle 13.97 3 492 2022-01-16 381 Online 29.49 4 492 2022-01-16 381 Online 48.75 4 492 2022-01-16 381 Online 29.51 3 493 2022-01-17 155 Online 13.97 3 493 2022-01-17 155 Online 38.28 3 494 2022-01-17 256 Online 29.55 3 494 2022-01-17 256 Online 16.64 2 495 2022-01-17 205 San Francisco 10.11 2 495 2022-01-17 205 San Francisco 19.16 2 495 2022-01-17 205 San Francisco 37.0 4 496 2022-01-17 33 New York City 30.69 5 496 2022-01-17 33 New York City 38.28 3 497 2022-01-18 164 Online 48.75 4 497 2022-01-18 164 Online 29.51 2 498 2022-01-18 262 Online 10.48 3 498 2022-01-18 262 Online 24.46 4 499 2022-01-18 333 Online 11.0 2 499 2022-01-18 333 Online 16.67 5 500 2022-01-18 200 Online 38.34 4 501 2022-01-18 367 Online 44.17 3 501 2022-01-18 367 Online 24.46 3 502 2022-01-19 355 Online 16.67 3 502 2022-01-19 355 Online 27.64 5 503 2022-01-20 243 Online 19.16 1 504 2022-01-21 107 Online 48.75 4 504 2022-01-21 107 Online 5.65 3 504 2022-01-21 107 Online 22.98 4 505 2022-01-22 248 Online 29.55 4 505 2022-01-22 248 Online 23.32 2 505 2022-01-22 248 Online 10.24 4 506 2022-01-22 4 Online 38.34 3 506 2022-01-22 4 Online 24.46 4 507 2022-01-22 137 Online 23.32 5 507 2022-01-22 137 Online 38.34 4 508 2022-01-22 157 Online 48.39 4 508 2022-01-22 157 Online 12.64 3 509 2022-01

In [0]:
# creating a total amount column at the record level
order_details = order_details.withColumn('TOTAL_SALES_AMOUNT', order_details['UNIT_PRICE']*order_details['QUANTITY'])

In [0]:
# reviewing the current state of the order_details dataframe
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME UNIT_PRICE QUANTITY TOTAL_SALES_AMOUNT 447 2022-01-06 355 Online 49.12 4 196.48 447 2022-01-06 355 Online 22.98 2 45.96 448 2022-01-06 155 Online 5.65 2 11.3 449 2022-01-06 242 Online 28.21 4 112.84 449 2022-01-06 242 Online 38.34 4 153.36 449 2022-01-06 242 Online 31.68 4 126.72 450 2022-01-06 49 Online 37.0 2 74.0 451 2022-01-06 204 Online 10.24 4 40.96 452 2022-01-07 216 Online 49.12 2 98.24 452 2022-01-07 216 Online 16.64 2 33.28 452 2022-01-07 216 Online 24.71 3 74.13 453 2022-01-07 4 New York City 29.55 2 59.1 453 2022-01-07 4 New York City 16.64 3 49.92 454 2022-01-07 388 Online 39.91 3 119.72999999999999 454 2022-01-07 388 Online 8.66 4 34.64 455 2022-01-07 291 Online 10.33 4 41.32 455 2022-01-07 291 Online 24.71 3 74.13 455 2022-01-07 291 Online 19.16 2 38.32 456 2022-01-08 272 Online 39.16 4 156.64 456 2022-01-08 272 Online 38.28 5 191.4 457 2022-01-08 307 Online 39.16 1 39.16 458 2022-01-08 42 Online 26.14 2 52.28 458 2022-01-08 42 Online 22.98 2 45.96 459 2022-01-09 390 Online 22.98 4 91.92 460 2022-01-09 235 Online 5.65 3 16.950000000000003 460 2022-01-09 235 Online 43.71 3 131.13 461 2022-01-09 302 Online 48.75 4 195.0 461 2022-01-09 302 Online 34.06 4 136.24 462 2022-01-09 357 Online 13.09 3 39.269999999999996 462 2022-01-09 357 Online 14.34 1 14.34 463 2022-01-09 271 Online 24.71 3 74.13 463 2022-01-09 271 Online 23.32 4 93.28 464 2022-01-09 79 Online 39.32 5 196.6 465 2022-01-09 280 Online 30.69 5 153.45000000000002 466 2022-01-10 210 Bucharest 27.64 4 110.56 466 2022-01-10 210 Bucharest 8.66 5 43.3 467 2022-01-11 293 Online 44.17 3 132.51 469 2022-01-12 239 Online 39.78 1 39.78 469 2022-01-12 239 Online 31.68 4 126.72 470 2022-01-12 217 Online 16.64 5 83.2 470 2022-01-12 217 Online 16.67 5 83.35000000000001 471 2022-01-12 61 Seattle 39.78 2 79.56 472 2022-01-12 182 Online 37.0 1 37.0 473 2022-01-12 116 Online 27.64 3 82.92 473 2022-01-12 116 Online 8.66 4 34.64 474 2022-01-12 244 Online 7.18 4 28.72 474 2022-01-12 244 Online 30.69 2 61.38 475 2022-01-12 210 Online 24.46 3 73.38 475 2022-01-12 210 Online 23.32 3 69.96000000000001 475 2022-01-12 210 Online 29.55 5 147.75 476 2022-01-12 84 Online 39.16 5 195.79999999999998 476 2022-01-12 84 Online 13.09 5 65.45 477 2022-01-13 374 Online 29.49 1 29.49 477 2022-01-13 374 Online 29.51 3 88.53 478 2022-01-13 389 Online 39.32 3 117.96000000000001 478 2022-01-13 389 Online 30.69 4 122.76 478 2022-01-13 389 Online 10.33 3 30.990000000000002 479 2022-01-13 368 Online 19.16 3 57.480000000000004 479 2022-01-13 368 Online 31.68 1 31.68 480 2022-01-13 344 Online 19.16 4 76.64 481 2022-01-13 118 Online 49.12 4 196.48 481 2022-01-13 118 Online 21.16 1 21.16 481 2022-01-13 118 Online 10.48 5 52.400000000000006 482 2022-01-13 88 Online 31.68 2 63.36 482 2022-01-13 88 Online 39.78 2 79.56 482 2022-01-13 88 Online 7.18 4 28.72 483 2022-01-13 72 Online 14.34 4 57.36 484 2022-01-14 159 Online 10.24 4 40.96 484 2022-01-14 159 Online 8.66 3 25.98 485 2022-01-15 134 Online 29.49 4 117.96 485 2022-01-15 134 Online 12.64 3 37.92 486 2022-01-15 105 Online 44.17 1 44.17 486 2022-01-15 105 Online 8.66 3 25.98 487 2022-01-15 259 Online 39.89 2 79.78 488 2022-01-15 150 Online 37.34 3 112.02000000000001 488 2022-01-15 150 Online 13.09 4 52.36 490 2022-01-16 48 Online 29.49 1 29.49 491 2022-01-16 264 Seattle 10.11 4 40.44 491 2022-01-16 264 Seattle 13.97 3 41.910000000000004 492 2022-01-16 381 Online 29.49 4 117.96 492 2022-01-16 381 Online 48.75 4 195.0 492 2022-01-16 381 Online 29.51 3 88.53 493 2022-01-17 155 Online 13.97 3 41.910000000000004 493 2022-01-17 155 Online 38.28 3 114.84 494 2022-01-17 256 Online 29.55 3 88.65 494 2022-01-17 256 Online 16.64 2 33.28 495 2022-01-17 205 San Francisco 10.11 2 20.22 495 2022-01-17 205 San Francisco 19.16 2 38.32 495 2022-01-17 205 San Francisco 37.0 4 148.0 496 2022-01-17 33 New York City 30.69 5 153.45000000000002 496 2022-01-17 33 New York City 38.28 3 114.84 497 2022-01-18 164 Online 48.75 4 195.0 497 2022-01-

In [0]:
# grouping the order_details dataframe and taking the sum of the total amount, renaming this to 'TOTAL_ORDER_AMOUNT'
# assigning the result back to the order_details dataframe
order_details = order_details. \
groupBy('ORDER_ID', 'DATE', 'CUSTOMER_ID', 'STORE_NAME'). \
sum('TOTAL_SALES_AMOUNT'). \
withColumnRenamed('sum(TOTAL_SALES_AMOUNT)', 'TOTAL_ORDER_AMOUNT')

In [0]:
# reviewing the current state of the order_details dataframe
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME TOTAL_ORDER_AMOUNT 524 2022-01-26 287 Online 28.68 158 2021-10-25 387 Online 200.03 294 2021-11-28 202 Online 220.73999999999998 343 2021-12-12 277 Online 213.29000000000002 1432 2022-07-14 337 Online 71.74 1544 2022-07-30 234 San Francisco 77.07 1721 2022-08-29 162 Perth 193.34 1748 2022-09-03 176 Online 163.54 746 2022-03-13 263 Online 45.66 802 2022-03-22 381 Online 101.16 859 2022-04-04 109 Online 377.67 896 2022-04-13 192 Online 194.62 1032 2022-05-05 280 Online 241.56 1091 2022-05-16 92 Chicago 95.24000000000001 102 2021-10-09 94 Online 188.98000000000002 1130 2022-05-24 247 New Dehli 12.64 1431 2022-07-14 166 Online 253.21000000000004 1594 2022-08-06 56 Online 54.56 1596 2022-08-06 148 Online 280.8 1664 2022-08-18 386 Utrecht 55.47 1095 2022-05-17 330 Online 150.68 411 2021-12-28 292 Online 198.28000000000003 1407 2022-07-10 76 S�o Paulo 200.91 1638 2022-08-13 135 Buenos Aires 60.36 1815 2022-09-14 79 Bejing 122.02000000000001 1886 2022-09-29 203 Tel Aviv 37.92 1930 2022-10-10 338 Buenos Aires 17.32 162 2021-10-27 392 Online 77.84 300 2021-11-29 80 Online 155.15 365 2021-12-19 350 Online 199.07 370 2021-12-20 31 San Francisco 230.90000000000003 1337 2022-06-28 73 Online 122.1 1592 2022-08-06 121 Online 51.41 1782 2022-09-08 300 Online 109.24000000000001 1804 2022-09-13 256 Online 366.61 1827 2022-09-17 310 Mexico City 138.82 1376 2022-07-06 382 Chicago 57.36 1480 2022-07-21 299 Online 163.2 1529 2022-07-28 71 Bengaluru 79.82 1657 2022-08-17 77 Online 30.990000000000002 1836 2022-09-19 267 Online 132.5 1852 2022-09-22 326 Online 172.07 1926 2022-10-09 366 S�o Paulo 268.81 31 2021-09-11 122 Online 225.87 86 2021-10-05 151 Online 345.1 171 2021-10-29 273 Online 223.68 229 2021-11-09 117 Online 170.24 327 2021-12-07 392 Online 124.07999999999998 1209 2022-06-09 283 Online 248.2 1276 2022-06-18 93 London 52.25 1490 2022-07-23 36 Bucharest 93.7 1630 2022-08-12 333 Mumbai 40.96 1814 2022-09-14 359 Online 46.64 1909 2022-10-04 345 Online 121.22 471 2022-01-12 61 Seattle 79.56 597 2022-02-13 269 Online 50.65 979 2022-04-27 43 Mumbai 61.38 983 2022-04-28 170 Online 203.07999999999998 17 2021-09-03 16 Online 351.64 93 2021-10-07 172 Online 261.68 438 2022-01-03 311 Online 213.93 1420 2022-07-12 215 Online 264.96000000000004 1558 2022-08-01 44 Online 254.18 1819 2022-09-15 22 Tokyo 148.38 449 2022-01-06 242 Online 392.9200000000001 497 2022-01-18 164 Online 254.02 609 2022-02-16 187 Online 185.0 739 2022-03-12 159 Online 369.15 786 2022-03-20 203 Online 30.900000000000002 849 2022-04-02 34 Online 47.7 995 2022-04-30 192 Online 56.5 1738 2022-09-01 376 Online 188.24 1824 2022-09-17 21 Bejing 184.57 618 2022-02-17 113 Online 176.76 954 2022-04-22 118 Online 121.31 123 2021-10-15 106 Online 86.89 208 2021-11-05 326 Online 37.34 1485 2022-07-22 157 Online 135.19 1523 2022-07-28 392 New Dehli 105.8 813 2022-03-26 383 London 98.24 833 2022-03-29 388 Online 256.34000000000003 930 2022-04-17 190 Online 116.6 190 2021-11-01 315 Online 41.910000000000004 244 2021-11-13 95 Online 56.870000000000005 1198 2022-06-07 119 Online 224.23000000000002 1362 2022-07-03 353 Chicago 104.77000000000001 1537 2022-07-30 91 Online 253.65 1580 2022-08-04 301 Online 156.12 1667 2022-08-19 304 Mumbai 96.51 1861 2022-09-23 292 Online 363.18 525 2022-01-26 43 Online 124.14 78 2021-10-02 20 Online 179.66 143 2021-10-21 348 Online 68.56 196 2021-11-03 8 Online 91.33000000000001 258 2021-11-18 162 Online 242.31000000000003 1321 2022-06-26 11 Online 180.26999999999998 1577 2022-08-04 208 Online 121.61000000000001 1727 2022-08-29 49 Mexico City 202.8 1866 2022-09-25 51 Tokyo 181.5 1893 2022-10-01 225 Tokyo 138.89 545 2022-01-31 35 Online 351.7 666 2022-02-27 336 Online 73.38 886 2022-04-09 54 Online 55.88 1085 2022-05-15 267 London 79.96000000000001 152 2021-10-24 300 Online 174.14999999999998 198 2021-11-03 319 Online 59.599999999999994 321 2021-12-06 283 Online 73.38 1317 2022-06-25 266 Online 278.39 1865 2022-09-24 224 Bejing 14

In [0]:
# rounding the TOTAL_ORDER_AMOUNT to 2 dp
order_details = order_details.withColumn('TOTAL_ORDER_AMOUNT', round('TOTAL_ORDER_AMOUNT',2))

In [0]:
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME TOTAL_ORDER_AMOUNT 524 2022-01-26 287 Online 28.68 158 2021-10-25 387 Online 200.03 294 2021-11-28 202 Online 220.74 343 2021-12-12 277 Online 213.29 1432 2022-07-14 337 Online 71.74 1544 2022-07-30 234 San Francisco 77.07 1721 2022-08-29 162 Perth 193.34 1748 2022-09-03 176 Online 163.54 746 2022-03-13 263 Online 45.66 802 2022-03-22 381 Online 101.16 859 2022-04-04 109 Online 377.67 896 2022-04-13 192 Online 194.62 1032 2022-05-05 280 Online 241.56 1091 2022-05-16 92 Chicago 95.24 102 2021-10-09 94 Online 188.98 1130 2022-05-24 247 New Dehli 12.64 1431 2022-07-14 166 Online 253.21 1594 2022-08-06 56 Online 54.56 1596 2022-08-06 148 Online 280.8 1664 2022-08-18 386 Utrecht 55.47 1095 2022-05-17 330 Online 150.68 411 2021-12-28 292 Online 198.28 1407 2022-07-10 76 S�o Paulo 200.91 1638 2022-08-13 135 Buenos Aires 60.36 1815 2022-09-14 79 Bejing 122.02 1886 2022-09-29 203 Tel Aviv 37.92 1930 2022-10-10 338 Buenos Aires 17.32 162 2021-10-27 392 Online 77.84 300 2021-11-29 80 Online 155.15 365 2021-12-19 350 Online 199.07 370 2021-12-20 31 San Francisco 230.9 1337 2022-06-28 73 Online 122.1 1592 2022-08-06 121 Online 51.41 1782 2022-09-08 300 Online 109.24 1804 2022-09-13 256 Online 366.61 1827 2022-09-17 310 Mexico City 138.82 1376 2022-07-06 382 Chicago 57.36 1480 2022-07-21 299 Online 163.2 1529 2022-07-28 71 Bengaluru 79.82 1657 2022-08-17 77 Online 30.99 1836 2022-09-19 267 Online 132.5 1852 2022-09-22 326 Online 172.07 1926 2022-10-09 366 S�o Paulo 268.81 31 2021-09-11 122 Online 225.87 86 2021-10-05 151 Online 345.1 171 2021-10-29 273 Online 223.68 229 2021-11-09 117 Online 170.24 327 2021-12-07 392 Online 124.08 1209 2022-06-09 283 Online 248.2 1276 2022-06-18 93 London 52.25 1490 2022-07-23 36 Bucharest 93.7 1630 2022-08-12 333 Mumbai 40.96 1814 2022-09-14 359 Online 46.64 1909 2022-10-04 345 Online 121.22 471 2022-01-12 61 Seattle 79.56 597 2022-02-13 269 Online 50.65 979 2022-04-27 43 Mumbai 61.38 983 2022-04-28 170 Online 203.08 17 2021-09-03 16 Online 351.64 93 2021-10-07 172 Online 261.68 438 2022-01-03 311 Online 213.93 1420 2022-07-12 215 Online 264.96 1558 2022-08-01 44 Online 254.18 1819 2022-09-15 22 Tokyo 148.38 449 2022-01-06 242 Online 392.92 497 2022-01-18 164 Online 254.02 609 2022-02-16 187 Online 185.0 739 2022-03-12 159 Online 369.15 786 2022-03-20 203 Online 30.9 849 2022-04-02 34 Online 47.7 995 2022-04-30 192 Online 56.5 1738 2022-09-01 376 Online 188.24 1824 2022-09-17 21 Bejing 184.57 618 2022-02-17 113 Online 176.76 954 2022-04-22 118 Online 121.31 123 2021-10-15 106 Online 86.89 208 2021-11-05 326 Online 37.34 1485 2022-07-22 157 Online 135.19 1523 2022-07-28 392 New Dehli 105.8 813 2022-03-26 383 London 98.24 833 2022-03-29 388 Online 256.34 930 2022-04-17 190 Online 116.6 190 2021-11-01 315 Online 41.91 244 2021-11-13 95 Online 56.87 1198 2022-06-07 119 Online 224.23 1362 2022-07-03 353 Chicago 104.77 1537 2022-07-30 91 Online 253.65 1580 2022-08-04 301 Online 156.12 1667 2022-08-19 304 Mumbai 96.51 1861 2022-09-23 292 Online 363.18 525 2022-01-26 43 Online 124.14 78 2021-10-02 20 Online 179.66 143 2021-10-21 348 Online 68.56 196 2021-11-03 8 Online 91.33 258 2021-11-18 162 Online 242.31 1321 2022-06-26 11 Online 180.27 1577 2022-08-04 208 Online 121.61 1727 2022-08-29 49 Mexico City 202.8 1866 2022-09-25 51 Tokyo 181.5 1893 2022-10-01 225 Tokyo 138.89 545 2022-01-31 35 Online 351.7 666 2022-02-27 336 Online 73.38 886 2022-04-09 54 Online 55.88 1085 2022-05-15 267 London 79.96 152 2021-10-24 300 Online 174.15 198 2021-11-03 319 Online 59.6 321 2021-12-06 283 Online 73.38 1317 2022-06-25 266 Online 278.39 1865 2022-09-24 224 Bejing 146.25 534 2022-01-28 362 Online 134.2 708 2022-03-07 203 Online 109.46 145 2021-10-22 254 Online 170.64 177 2021-10-30 179 Online 41.91 212 2021-11-06 381 Online 231.32 345 2021-12-12 311 Online 26.14 1425 2022-07-13 190 Sydney 290.54 1459 2022-07-19 207 Online 276.91 1622 2022-08-10 59 Online 69.31 1636 2022-08-13 366 Online 85.3

In [0]:
# writing the order_details dataframe as a parquet file in the gold layer
order_details.write.parquet('/FileStore/tables/gold/order_details', mode='overwrite')


#### MONTHLY_SALES

Create an aggregated table to show the monthly sales total and save it in the gold layer as a parquet file called MONTHLY_SALES.

The table should have two columns:
- MONTH_YEAR - this should be in the format yyyy-MM e.g. 2020-10
- TOTAL_SALES

Display the sales total rounded to 2 dp and sorted in descending date order.

In [0]:
# can use the date columns from the order_details table
order_details.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME TOTAL_ORDER_AMOUNT 524 2022-01-26 287 Online 28.68 158 2021-10-25 387 Online 200.03 294 2021-11-28 202 Online 220.74 343 2021-12-12 277 Online 213.29 1432 2022-07-14 337 Online 71.74 1544 2022-07-30 234 San Francisco 77.07 1721 2022-08-29 162 Perth 193.34 1748 2022-09-03 176 Online 163.54 746 2022-03-13 263 Online 45.66 802 2022-03-22 381 Online 101.16 859 2022-04-04 109 Online 377.67 896 2022-04-13 192 Online 194.62 1032 2022-05-05 280 Online 241.56 1091 2022-05-16 92 Chicago 95.24 102 2021-10-09 94 Online 188.98 1130 2022-05-24 247 New Dehli 12.64 1431 2022-07-14 166 Online 253.21 1594 2022-08-06 56 Online 54.56 1596 2022-08-06 148 Online 280.8 1664 2022-08-18 386 Utrecht 55.47 1095 2022-05-17 330 Online 150.68 411 2021-12-28 292 Online 198.28 1407 2022-07-10 76 S�o Paulo 200.91 1638 2022-08-13 135 Buenos Aires 60.36 1815 2022-09-14 79 Bejing 122.02 1886 2022-09-29 203 Tel Aviv 37.92 1930 2022-10-10 338 Buenos Aires 17.32 162 2021-10-27 392 Online 77.84 300 2021-11-29 80 Online 155.15 365 2021-12-19 350 Online 199.07 370 2021-12-20 31 San Francisco 230.9 1337 2022-06-28 73 Online 122.1 1592 2022-08-06 121 Online 51.41 1782 2022-09-08 300 Online 109.24 1804 2022-09-13 256 Online 366.61 1827 2022-09-17 310 Mexico City 138.82 1376 2022-07-06 382 Chicago 57.36 1480 2022-07-21 299 Online 163.2 1529 2022-07-28 71 Bengaluru 79.82 1657 2022-08-17 77 Online 30.99 1836 2022-09-19 267 Online 132.5 1852 2022-09-22 326 Online 172.07 1926 2022-10-09 366 S�o Paulo 268.81 31 2021-09-11 122 Online 225.87 86 2021-10-05 151 Online 345.1 171 2021-10-29 273 Online 223.68 229 2021-11-09 117 Online 170.24 327 2021-12-07 392 Online 124.08 1209 2022-06-09 283 Online 248.2 1276 2022-06-18 93 London 52.25 1490 2022-07-23 36 Bucharest 93.7 1630 2022-08-12 333 Mumbai 40.96 1814 2022-09-14 359 Online 46.64 1909 2022-10-04 345 Online 121.22 471 2022-01-12 61 Seattle 79.56 597 2022-02-13 269 Online 50.65 979 2022-04-27 43 Mumbai 61.38 983 2022-04-28 170 Online 203.08 17 2021-09-03 16 Online 351.64 93 2021-10-07 172 Online 261.68 438 2022-01-03 311 Online 213.93 1420 2022-07-12 215 Online 264.96 1558 2022-08-01 44 Online 254.18 1819 2022-09-15 22 Tokyo 148.38 449 2022-01-06 242 Online 392.92 497 2022-01-18 164 Online 254.02 609 2022-02-16 187 Online 185.0 739 2022-03-12 159 Online 369.15 786 2022-03-20 203 Online 30.9 849 2022-04-02 34 Online 47.7 995 2022-04-30 192 Online 56.5 1738 2022-09-01 376 Online 188.24 1824 2022-09-17 21 Bejing 184.57 618 2022-02-17 113 Online 176.76 954 2022-04-22 118 Online 121.31 123 2021-10-15 106 Online 86.89 208 2021-11-05 326 Online 37.34 1485 2022-07-22 157 Online 135.19 1523 2022-07-28 392 New Dehli 105.8 813 2022-03-26 383 London 98.24 833 2022-03-29 388 Online 256.34 930 2022-04-17 190 Online 116.6 190 2021-11-01 315 Online 41.91 244 2021-11-13 95 Online 56.87 1198 2022-06-07 119 Online 224.23 1362 2022-07-03 353 Chicago 104.77 1537 2022-07-30 91 Online 253.65 1580 2022-08-04 301 Online 156.12 1667 2022-08-19 304 Mumbai 96.51 1861 2022-09-23 292 Online 363.18 525 2022-01-26 43 Online 124.14 78 2021-10-02 20 Online 179.66 143 2021-10-21 348 Online 68.56 196 2021-11-03 8 Online 91.33 258 2021-11-18 162 Online 242.31 1321 2022-06-26 11 Online 180.27 1577 2022-08-04 208 Online 121.61 1727 2022-08-29 49 Mexico City 202.8 1866 2022-09-25 51 Tokyo 181.5 1893 2022-10-01 225 Tokyo 138.89 545 2022-01-31 35 Online 351.7 666 2022-02-27 336 Online 73.38 886 2022-04-09 54 Online 55.88 1085 2022-05-15 267 London 79.96 152 2021-10-24 300 Online 174.15 198 2021-11-03 319 Online 59.6 321 2021-12-06 283 Online 73.38 1317 2022-06-25 266 Online 278.39 1865 2022-09-24 224 Bejing 146.25 534 2022-01-28 362 Online 134.2 708 2022-03-07 203 Online 109.46 145 2021-10-22 254 Online 170.64 177 2021-10-30 179 Online 41.91 212 2021-11-06 381 Online 231.32 345 2021-12-12 311 Online 26.14 1425 2022-07-13 190 Sydney 290.54 1459 2022-07-19 207 Online 276.91 1622 2022-08-10 59 Online 69.31 1636 2022-08-13 366 Online 85.3

In [0]:
# creating a column that extracts the month and year from the date column
# assigning the dataframe result back to the sales_with_month variable
# https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.functions.date_format.html?highlight=date_format#pyspark.sql.functions.date_format
sales_with_month = order_details.withColumn('MONTH_YEAR', date_format('DATE','yyyy-MM'))

In [0]:
sales_with_month.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME TOTAL_ORDER_AMOUNT MONTH_YEAR 524 2022-01-26 287 Online 28.68 2022-01 158 2021-10-25 387 Online 200.03 2021-10 294 2021-11-28 202 Online 220.74 2021-11 343 2021-12-12 277 Online 213.29 2021-12 1432 2022-07-14 337 Online 71.74 2022-07 1544 2022-07-30 234 San Francisco 77.07 2022-07 1721 2022-08-29 162 Perth 193.34 2022-08 1748 2022-09-03 176 Online 163.54 2022-09 746 2022-03-13 263 Online 45.66 2022-03 802 2022-03-22 381 Online 101.16 2022-03 859 2022-04-04 109 Online 377.67 2022-04 896 2022-04-13 192 Online 194.62 2022-04 1032 2022-05-05 280 Online 241.56 2022-05 1091 2022-05-16 92 Chicago 95.24 2022-05 102 2021-10-09 94 Online 188.98 2021-10 1130 2022-05-24 247 New Dehli 12.64 2022-05 1431 2022-07-14 166 Online 253.21 2022-07 1594 2022-08-06 56 Online 54.56 2022-08 1596 2022-08-06 148 Online 280.8 2022-08 1664 2022-08-18 386 Utrecht 55.47 2022-08 1095 2022-05-17 330 Online 150.68 2022-05 411 2021-12-28 292 Online 198.28 2021-12 1407 2022-07-10 76 S�o Paulo 200.91 2022-07 1638 2022-08-13 135 Buenos Aires 60.36 2022-08 1815 2022-09-14 79 Bejing 122.02 2022-09 1886 2022-09-29 203 Tel Aviv 37.92 2022-09 1930 2022-10-10 338 Buenos Aires 17.32 2022-10 162 2021-10-27 392 Online 77.84 2021-10 300 2021-11-29 80 Online 155.15 2021-11 365 2021-12-19 350 Online 199.07 2021-12 370 2021-12-20 31 San Francisco 230.9 2021-12 1337 2022-06-28 73 Online 122.1 2022-06 1592 2022-08-06 121 Online 51.41 2022-08 1782 2022-09-08 300 Online 109.24 2022-09 1804 2022-09-13 256 Online 366.61 2022-09 1827 2022-09-17 310 Mexico City 138.82 2022-09 1376 2022-07-06 382 Chicago 57.36 2022-07 1480 2022-07-21 299 Online 163.2 2022-07 1529 2022-07-28 71 Bengaluru 79.82 2022-07 1657 2022-08-17 77 Online 30.99 2022-08 1836 2022-09-19 267 Online 132.5 2022-09 1852 2022-09-22 326 Online 172.07 2022-09 1926 2022-10-09 366 S�o Paulo 268.81 2022-10 31 2021-09-11 122 Online 225.87 2021-09 86 2021-10-05 151 Online 345.1 2021-10 171 2021-10-29 273 Online 223.68 2021-10 229 2021-11-09 117 Online 170.24 2021-11 327 2021-12-07 392 Online 124.08 2021-12 1209 2022-06-09 283 Online 248.2 2022-06 1276 2022-06-18 93 London 52.25 2022-06 1490 2022-07-23 36 Bucharest 93.7 2022-07 1630 2022-08-12 333 Mumbai 40.96 2022-08 1814 2022-09-14 359 Online 46.64 2022-09 1909 2022-10-04 345 Online 121.22 2022-10 471 2022-01-12 61 Seattle 79.56 2022-01 597 2022-02-13 269 Online 50.65 2022-02 979 2022-04-27 43 Mumbai 61.38 2022-04 983 2022-04-28 170 Online 203.08 2022-04 17 2021-09-03 16 Online 351.64 2021-09 93 2021-10-07 172 Online 261.68 2021-10 438 2022-01-03 311 Online 213.93 2022-01 1420 2022-07-12 215 Online 264.96 2022-07 1558 2022-08-01 44 Online 254.18 2022-08 1819 2022-09-15 22 Tokyo 148.38 2022-09 449 2022-01-06 242 Online 392.92 2022-01 497 2022-01-18 164 Online 254.02 2022-01 609 2022-02-16 187 Online 185.0 2022-02 739 2022-03-12 159 Online 369.15 2022-03 786 2022-03-20 203 Online 30.9 2022-03 849 2022-04-02 34 Online 47.7 2022-04 995 2022-04-30 192 Online 56.5 2022-04 1738 2022-09-01 376 Online 188.24 2022-09 1824 2022-09-17 21 Bejing 184.57 2022-09 618 2022-02-17 113 Online 176.76 2022-02 954 2022-04-22 118 Online 121.31 2022-04 123 2021-10-15 106 Online 86.89 2021-10 208 2021-11-05 326 Online 37.34 2021-11 1485 2022-07-22 157 Online 135.19 2022-07 1523 2022-07-28 392 New Dehli 105.8 2022-07 813 2022-03-26 383 London 98.24 2022-03 833 2022-03-29 388 Online 256.34 2022-03 930 2022-04-17 190 Online 116.6 2022-04 190 2021-11-01 315 Online 41.91 2021-11 244 2021-11-13 95 Online 56.87 2021-11 1198 2022-06-07 119 Online 224.23 2022-06 1362 2022-07-03 353 Chicago 104.77 2022-07 1537 2022-07-30 91 Online 253.65 2022-07 1580 2022-08-04 301 Online 156.12 2022-08 1667 2022-08-19 304 Mumbai 96.51 2022-08 1861 2022-09-23 292 Online 363.18 2022-09 525 2022-01-26 43 Online 124.14 2022-01 78 2021-10-02 20 Online 179.66 2021-10 143 2021-10-21 348 Online 68.56 2021-10 196 2021-11-03 8 Online 91.33 2021-11 258 2021-11-18 162 Online 242.31 2021-11 1321 2022-06-2

In [0]:
monthly_sales = sales_with_month.groupBy('MONTH_YEAR').sum('TOTAL_ORDER_AMOUNT'). \
withColumn('TOTAL_SALES', round('sum(TOTAL_ORDER_AMOUNT)',2)).sort(sales_with_month['MONTH_YEAR'].desc()). \
select('MONTH_YEAR', 'TOTAL_SALES')

In [0]:
monthly_sales.display()

MONTH_YEAR TOTAL_SALES 2022-10 8214.0 2022-09 23970.29 2022-08 26180.9 2022-07 32217.2 2022-06 27184.09 2022-05 26848.93 2022-04 23223.25 2022-03 25424.28 2022-02 21488.51 2022-01 18116.82 2021-12 18992.43 2021-11 19334.15 2021-10 17908.78 2021-09 8660.46 2021-08 2125.53

In [0]:
# writing the monthly_sales dataframe as a parquet file in the gold layer
monthly_sales.write.parquet('/mnt/gold/monthly_sales', mode='overwrite')


#### STORE_MONTHLY_SALES

Create an aggregated table to show the monthly sales total by store and save it in the gold layer as a parquet file called STORE_MONTHLY_SALES.

The table should have two columns:
- MONTH_YEAR - this should be in the format yyyy-MM e.g. 2020-10
- STORE NAME
- TOTAL_SALES

Display the sales total rounded to 2 dp and sorted in descending date order.

In [0]:
# we can leverage the intermediate dataframe called sales_with_month to extract the information we need
sales_with_month.display()

ORDER_ID DATE CUSTOMER_ID STORE_NAME TOTAL_ORDER_AMOUNT MONTH_YEAR 524 2022-01-26 287 Online 28.68 2022-01 158 2021-10-25 387 Online 200.03 2021-10 294 2021-11-28 202 Online 220.74 2021-11 343 2021-12-12 277 Online 213.29 2021-12 1432 2022-07-14 337 Online 71.74 2022-07 1544 2022-07-30 234 San Francisco 77.07 2022-07 1721 2022-08-29 162 Perth 193.34 2022-08 1748 2022-09-03 176 Online 163.54 2022-09 746 2022-03-13 263 Online 45.66 2022-03 802 2022-03-22 381 Online 101.16 2022-03 859 2022-04-04 109 Online 377.67 2022-04 896 2022-04-13 192 Online 194.62 2022-04 1032 2022-05-05 280 Online 241.56 2022-05 1091 2022-05-16 92 Chicago 95.24 2022-05 102 2021-10-09 94 Online 188.98 2021-10 1130 2022-05-24 247 New Dehli 12.64 2022-05 1431 2022-07-14 166 Online 253.21 2022-07 1594 2022-08-06 56 Online 54.56 2022-08 1596 2022-08-06 148 Online 280.8 2022-08 1664 2022-08-18 386 Utrecht 55.47 2022-08 1095 2022-05-17 330 Online 150.68 2022-05 411 2021-12-28 292 Online 198.28 2021-12 1407 2022-07-10 76 S�o Paulo 200.91 2022-07 1638 2022-08-13 135 Buenos Aires 60.36 2022-08 1815 2022-09-14 79 Bejing 122.02 2022-09 1886 2022-09-29 203 Tel Aviv 37.92 2022-09 1930 2022-10-10 338 Buenos Aires 17.32 2022-10 162 2021-10-27 392 Online 77.84 2021-10 300 2021-11-29 80 Online 155.15 2021-11 365 2021-12-19 350 Online 199.07 2021-12 370 2021-12-20 31 San Francisco 230.9 2021-12 1337 2022-06-28 73 Online 122.1 2022-06 1592 2022-08-06 121 Online 51.41 2022-08 1782 2022-09-08 300 Online 109.24 2022-09 1804 2022-09-13 256 Online 366.61 2022-09 1827 2022-09-17 310 Mexico City 138.82 2022-09 1376 2022-07-06 382 Chicago 57.36 2022-07 1480 2022-07-21 299 Online 163.2 2022-07 1529 2022-07-28 71 Bengaluru 79.82 2022-07 1657 2022-08-17 77 Online 30.99 2022-08 1836 2022-09-19 267 Online 132.5 2022-09 1852 2022-09-22 326 Online 172.07 2022-09 1926 2022-10-09 366 S�o Paulo 268.81 2022-10 31 2021-09-11 122 Online 225.87 2021-09 86 2021-10-05 151 Online 345.1 2021-10 171 2021-10-29 273 Online 223.68 2021-10 229 2021-11-09 117 Online 170.24 2021-11 327 2021-12-07 392 Online 124.08 2021-12 1209 2022-06-09 283 Online 248.2 2022-06 1276 2022-06-18 93 London 52.25 2022-06 1490 2022-07-23 36 Bucharest 93.7 2022-07 1630 2022-08-12 333 Mumbai 40.96 2022-08 1814 2022-09-14 359 Online 46.64 2022-09 1909 2022-10-04 345 Online 121.22 2022-10 471 2022-01-12 61 Seattle 79.56 2022-01 597 2022-02-13 269 Online 50.65 2022-02 979 2022-04-27 43 Mumbai 61.38 2022-04 983 2022-04-28 170 Online 203.08 2022-04 17 2021-09-03 16 Online 351.64 2021-09 93 2021-10-07 172 Online 261.68 2021-10 438 2022-01-03 311 Online 213.93 2022-01 1420 2022-07-12 215 Online 264.96 2022-07 1558 2022-08-01 44 Online 254.18 2022-08 1819 2022-09-15 22 Tokyo 148.38 2022-09 449 2022-01-06 242 Online 392.92 2022-01 497 2022-01-18 164 Online 254.02 2022-01 609 2022-02-16 187 Online 185.0 2022-02 739 2022-03-12 159 Online 369.15 2022-03 786 2022-03-20 203 Online 30.9 2022-03 849 2022-04-02 34 Online 47.7 2022-04 995 2022-04-30 192 Online 56.5 2022-04 1738 2022-09-01 376 Online 188.24 2022-09 1824 2022-09-17 21 Bejing 184.57 2022-09 618 2022-02-17 113 Online 176.76 2022-02 954 2022-04-22 118 Online 121.31 2022-04 123 2021-10-15 106 Online 86.89 2021-10 208 2021-11-05 326 Online 37.34 2021-11 1485 2022-07-22 157 Online 135.19 2022-07 1523 2022-07-28 392 New Dehli 105.8 2022-07 813 2022-03-26 383 London 98.24 2022-03 833 2022-03-29 388 Online 256.34 2022-03 930 2022-04-17 190 Online 116.6 2022-04 190 2021-11-01 315 Online 41.91 2021-11 244 2021-11-13 95 Online 56.87 2021-11 1198 2022-06-07 119 Online 224.23 2022-06 1362 2022-07-03 353 Chicago 104.77 2022-07 1537 2022-07-30 91 Online 253.65 2022-07 1580 2022-08-04 301 Online 156.12 2022-08 1667 2022-08-19 304 Mumbai 96.51 2022-08 1861 2022-09-23 292 Online 363.18 2022-09 525 2022-01-26 43 Online 124.14 2022-01 78 2021-10-02 20 Online 179.66 2021-10 143 2021-10-21 348 Online 68.56 2021-10 196 2021-11-03 8 Online 91.33 2021-11 258 2021-11-18 162 Online 242.31 2021-11 1321 2022-06-2

In [0]:
# in addition to month_year you must also group by store_name
store_monthly_sales = sales_with_month.groupBy('MONTH_YEAR', 'STORE_NAME').sum('TOTAL_ORDER_AMOUNT'). \
withColumn('TOTAL_SALES', round('sum(TOTAL_ORDER_AMOUNT)',2)).sort(sales_with_month['MONTH_YEAR'].desc()). \
select('MONTH_YEAR','STORE_NAME', 'TOTAL_SALES')

In [0]:
store_monthly_sales.display()

MONTH_YEAR STORE_NAME TOTAL_SALES 2022-10 S�o Paulo 268.81 2022-10 Tel Aviv 3484.76 2022-10 Online 933.25 2022-10 Tokyo 1770.14 2022-10 Buenos Aires 462.63 2022-10 Mumbai 96.2 2022-10 Bejing 601.05 2022-10 Seattle 31.44 2022-10 Mexico City 565.72 2022-09 Tel Aviv 972.43 2022-09 S�o Paulo 663.2 2022-09 Berlin 481.98 2022-09 Bucharest 362.77 2022-09 Bejing 3248.28 2022-09 Sydney 1248.37 2022-09 Utrecht 573.63 2022-09 Online 7574.7 2022-09 Bengaluru 456.32 2022-09 Mexico City 2832.76 2022-09 New Dehli 490.0 2022-09 New York City 111.91 2022-09 Tokyo 1493.68 2022-09 Chicago 97.02 2022-09 Buenos Aires 1697.95 2022-09 Perth 904.12 2022-09 London 157.28 2022-09 Mumbai 603.89 2022-08 Berlin 300.06 2022-08 London 439.7 2022-08 Bengaluru 365.8 2022-08 Mexico City 671.94 2022-08 Sydney 1134.03 2022-08 Lagos 332.66 2022-08 Perth 1476.79 2022-08 Madrid 707.16 2022-08 S�o Paulo 1064.71 2022-08 Utrecht 357.1 2022-08 Online 14697.79 2022-08 Buenos Aires 1067.31 2022-08 Mumbai 1269.73 2022-08 Bucharest 498.64 2022-08 Chicago 289.09 2022-08 Seattle 543.7 2022-08 New Dehli 457.19 2022-08 Johannesburg 507.5 2022-07 Lagos 790.96 2022-07 New Dehli 2862.04 2022-07 Buenos Aires 267.83 2022-07 Berlin 281.7 2022-07 Perth 1037.38 2022-07 Johannesburg 1108.3 2022-07 Madrid 470.51 2022-07 Bengaluru 1637.74 2022-07 San Francisco 619.37 2022-07 S�o Paulo 990.31 2022-07 Utrecht 225.99 2022-07 Sydney 1667.46 2022-07 Online 16882.01 2022-07 Mumbai 1457.46 2022-07 Chicago 415.17 2022-07 New York City 440.02 2022-07 Bucharest 379.24 2022-07 London 683.71 2022-06 Chicago 35.61 2022-06 Utrecht 961.48 2022-06 Lagos 1607.5 2022-06 New York City 354.12 2022-06 Sydney 555.96 2022-06 Johannesburg 826.73 2022-06 Mumbai 260.78 2022-06 Bengaluru 1397.21 2022-06 Madrid 1430.32 2022-06 Seattle 209.62 2022-06 San Francisco 670.48 2022-06 S�o Paulo 161.19 2022-06 London 758.89 2022-06 Berlin 325.43 2022-06 New Dehli 965.43 2022-06 Online 16173.59 2022-06 Bucharest 200.55 2022-06 Perth 289.2 2022-05 New Dehli 517.1 2022-05 Chicago 413.56 2022-05 Johannesburg 179.96 2022-05 Berlin 668.22 2022-05 New York City 492.02 2022-05 Seattle 570.09 2022-05 Bucharest 616.67 2022-05 Online 18335.86 2022-05 Utrecht 1023.87 2022-05 Madrid 949.34 2022-05 Mumbai 683.07 2022-05 Bengaluru 224.75 2022-05 Lagos 707.91 2022-05 London 748.22 2022-05 San Francisco 718.29 2022-04 New York City 807.43 2022-04 Lagos 136.0 2022-04 London 784.71 2022-04 Berlin 920.63 2022-04 Utrecht 236.05 2022-04 Chicago 810.04 2022-04 Bucharest 601.08 2022-04 San Francisco 648.02 2022-04 Johannesburg 660.27 2022-04 Madrid 242.42 2022-04 Mumbai 72.68 2022-04 Online 17187.56 2022-04 Seattle 116.36 2022-03 Johannesburg 588.22 2022-03 Utrecht 325.73 2022-03 Lagos 472.46 2022-03 Madrid 305.68 2022-03 New York City 177.44 2022-03 Bucharest 835.02 2022-03 Berlin 688.51 2022-03 Chicago 1163.18 2022-03 Online 19474.33 2022-03 London 170.1 2022-03 San Francisco 179.8 2022-03 Seattle 1043.81 2022-02 Utrecht 213.76 2022-02 Online 18795.72 2022-02 Seattle 1006.89 2022-02 New York City 487.32 2022-02 London 139.42 2022-02 Chicago 209.51 2022-02 Berlin 124.58 2022-02 Madrid 82.45 2022-02 San Francisco 428.86 2022-01 San Francisco 542.67 2022-01 Bucharest 439.44 2022-01 New York City 377.31 2022-01 Utrecht 16.95 2022-01 London 524.8 2022-01 Online 15573.99 2022-01 Chicago 257.38 2022-01 Seattle 384.28 2021-12 San Francisco 390.08 2021-12 Seattle 79.65 2021-12 London 20.66 2021-12 New York City 124.52 2021-12 Chicago 30.72 2021-12 Bucharest 194.8 2021-12 Online 18152.0 2021-11 San Francisco 183.34 2021-11 Online 18916.95 2021-11 New York City 176.68 2021-11 Seattle 57.18 2021-10 Online 17875.22 2021-10 New York City 33.56 2021-09 Seattle 251.18 2021-09 Online 8409.28 2021-08 Online 2125.53

In [0]:
# writing the store_monthly_sales dataframe as a parquet file in the gold layer
store_monthly_sales.write.parquet('/mnt/gold/store_monthly_sales', mode='overwrite')